# Introduction

The goal of this notebook is to produce two stars of equal mass orbiting eachother in Newtonian physics. It should be trivially extensible to stars that are not equal mass and to solar systems with one planet. 

In newtonian gravity in space (as opposed to on the surface of the Earth, where the size of the Earth is so overwhelming compared to how far you walk that the gravitational field doesn't appear to change), stars orbit around eachother in circles or ellipses. It is also possible to have parabolic or hyperbolic orbits that are unbound. Gravity is a central force, and forces come in equal and opposite pairs. As a result, for equal mass motion, the stars motions are symmetric about a center point. 

While it is ideal to be able to compute hyperbolic, parabolic, and elliptical orbits, initially I will focus on circular orbits. 

Why would I do this, you might ask, given that circular orbits can be trivially computed with a little algebra in about the sixth week of the first year of freshman physics at the college level? 
- Because once I have a differential equation solver I can move on to orbits of more than two stars, which is interesting for stellar physics, globular clusters, exoplanets, and galactic dynamics. 
- Because it will help me demo my code in a simpler context than general relativity. 
- Because it is fun. 
- Because it is good coding practice and I need to pass a code test in industry and I've been out of the field for a year while I worked as a volunteer teacher. 

Here's the computation of the initial conditions, which is also a solution for the whole orbit for circular orbits.

Centripital force F_1=m_1*v^2/r
Newtonain Gravitational Force F_1=G*m_1*m_2/r^2

Setting the two forces equal, v=sqrt(m_2/r)

By Newtons laws m_1*a_1=F_1

Setting that equal to the gravitational force

a_1=G*m_2/r^2

And that's all you need unless you transform to the reduced mass coordinate system where one mass is held fixed at the center. Normally both masses have to be evolved around eachother with equal and opposite force pairs. I use this computation for my initial conditions, but solve the orbit numerically using a differential equation solver, either Euler or Runga Kutta 4th order.

The orbits should conserve energy. E=1/2*m1*v1^2+ 1/2*m2*v2*2 -G*m1*m2/r^2

The orbits should conserve angular momentum. L=m1*v1*r+m2*v2*r

The orbits should preserve orbital radius if they're circular. 

The focus of an ellipse, hyperbola, or parabola should be at the center of mass of the orbit (half way between two bodies of equal mass).

# Differential equation solvers

In [1]:
#from pip._internal import main as pip_main
#except ImportError:
#    from pip._internal import main as pip_main

#package_to_install = "numpy"
#try:
#    pip_main(["install", "--user", package_to_install])
#except SystemExit as e:
#    print(e)

The Newtonian Gravitational Force depends upon the masses of the two objects and the square of the distances between them. When one astronomical body acts upon another with force F12, the second body acts upon the first with equal and opposite force F21=-F12. Gravitational Force follows an inverse square law with regard to distance scaling that is exact in Newtonian gravity.

In [2]:
import numpy as np
import matplotlib.pyplot as plt

def NewtonianForce(mass1,mass2, r):
    return (6.67408*10**-11)*mass1*mass2/r/r;

To compute an orbit, it is necessary to solve a second order differential equation. 

F=ma

For a two body problem:

F12x=m1 d^2 x1/dt^2

This can be decomposed into two coupled differential equations.

F12x= m1 d v1/dt

v1= d x1/dt

There is also a y component and a z component. 
It is also necessary to track the position of the second particle.

Recall that once a force F12 is split into its components in the x and y direction, F12 will no longer exactly be given by the NewtonainForce equation given above but rather the magnitude of F12x, F12y, and F12z combined will equal that total. The nagnitude of a vector is found by squaring and summing the components then taking the square roots. So, sqrt(F12x^2+F12y^2+F12z^2)=FNewtonianForce

Assume, for the purposes of a two body problem, the orbit is confined to the x-y plane. 

Define polar coordinates phi in the x-y plane beginning from the x axis and proceeding toward the y axis. Then F12x=F12 cos phi and F12y= F12 sin phi.

F12x=x/sqrt(x^2+y^2)*F12

F12y = y/sqrt(x^2+y^2)*F12

# Numerical solutions to differential equations

To integrate a differential equation numerically, simply differentiate both of the two coupled equations, one time steop at a time, numerically. But how is this done numerically? There are a couple of ways. First consider how a derivative is defined. A derivative is a limit of a difference divided by a timestep. The euler derivative makes this definition discrete for small time steps. 

In [3]:
def euler(h,t, x,y,z,f,debugprint):
    xstep = (f(t, x, y,z)+f(t+h,x+h,y,z))/2*h
    xnew=x+xstep
    if(debugprint):
        print(h,t,x,xstep,xnew)
    return t+h,xnew

The euler routine essentially just finds the slope in a small region of the graph. 

The Runga Kutta numerical derivative is a fourth order approximation to the derivative that accounts for the curvature and is better for something like an orbit that fundamentally has curvature to it where orvershoot near a minima may matter. 

# Verify Euler numerically

In [4]:
def polynomial(x,power,a):
    p=a*x**power
    #print(pi)
    return p
    

def polymaker1(t,x,y,z,power,a):
    def poly(t,x,y,z):
        return polynomial(x,power,a)
    return poly

#exact solution to pow=1 is lnx

In [5]:
import numpy as np
t=0.
x=1.
y=1.
z=1.
print(t,x)
polyfn=polymaker1(t,x,y,z,1,1.0)

0.0 1.0


In [6]:
outp=polyfn(t,x,y,z) #this is correct: x^2
print(outp)

1.0


In [7]:
eulerpolyout=euler(.01,t,x,y,z,polyfn,True)
print(eulerpolyout)

0.01 0.0 1.0 0.01005 1.01005
(0.01, 1.01005)


In [8]:
dt=0.01
numsteps=10
xvals=[]
tvals=[]
for i in np.arange(1,numsteps):
    #t=0.+i*dt
    t,x=euler(dt,t,x,y,z,polyfn,True)
    print(x)
    xvals.append(x)
    tvals.append(t)
print(xvals)
print(tvals)

0.01 0.0 1.0 0.01005 1.01005
1.01005
0.01 0.01 1.01005 0.0101505 1.0202004999999998
1.0202004999999998
0.01 0.02 1.0202004999999998 0.010252005 1.0304525049999997
1.0304525049999997
0.01 0.03 1.0304525049999997 0.010354525049999999 1.0408070300499996
1.0408070300499996
0.01 0.04 1.0408070300499996 0.010458070300499998 1.0512651003504996
1.0512651003504996
0.01 0.05 1.0512651003504996 0.010562651003504998 1.0618277513540046
1.0618277513540046
0.01 0.060000000000000005 1.0618277513540046 0.010668277513540048 1.0724960288675447
1.0724960288675447
0.01 0.07 1.0724960288675447 0.010774960288675448 1.0832709891562202
1.0832709891562202
0.01 0.08 1.0832709891562202 0.010882709891562202 1.0941536990477825
1.0941536990477825
[1.01005, 1.0202004999999998, 1.0304525049999997, 1.0408070300499996, 1.0512651003504996, 1.0618277513540046, 1.0724960288675447, 1.0832709891562202, 1.0941536990477825]
[0.01, 0.02, 0.03, 0.04, 0.05, 0.060000000000000005, 0.07, 0.08, 0.09]


In [9]:
def analyticsoln1(array):
        returnarray=np.exp(array)
        return returnarray
analyticxvals=analyticsoln1(tvals)
print(analyticxvals)

[1.01005017 1.02020134 1.03045453 1.04081077 1.0512711  1.06183655
 1.07250818 1.08328707 1.09417428]


# Implement RK4

In [10]:
def RK4(h,t,x,y,z,f,printdebug): #not a finite difference so no step in y
    k1= h*f(t,x,y,z)
    k2=h*f(t+h/2.,x+k1/2.,y,z)
    k3=h*f(t+h/2.,x+k2/2.,y,z)
    k4=h*f(t+h,x+k3,y,z)
    if(printdebug):
        print(f(t,x,y,z))
        print(t,x,y,z,h) 
        print("k1",k1)
        print("k2",k2)
        print("k3",k3)
        print("k4",k4)
        print(1./6.*(k1+2.*k2+2.*k3+k4))
        print(x+1/6.*(k1+2.*k2+2.*k3+k4))
    return t+h, x+1/6.*(k1+2.*k2+2.*k3+k4)



In [11]:
def RK4nodebug(h,t,x,y,z,f): #not a finite difference so no step in y
    k1= h*f(t,x,y,z)
    #print("k1",k1)
    k2=h*f(t+h/2.,x+k1/2.,y,z)
    #print("k2",k2)
    k3=h*f(t+h/2.,x+k2/2.,y,z)
    #print("k3",k3)
    k4=h*f(t+h,x+k3,y,z)
    #print("k4",k4)
    return t+h, x+1/6.*(k1+2.*k2+2.*k3+k4)



# Verifying the RK4 routine numerically

First I verify the RK4 by examining the behavior for a differential equation where the right hand side is a fourth order polynomial. This should have a truncation error that is on the order of the fourth order polynomial itself

In [12]:
def polynomial4(t,x,a,b,c,d,e):
    p=a*t**4+b*t**3+c*t**2+d*t+e
    #print(pi)
    return p
    

def polymaker(t,x,y,z,a,b,c,d,e):
    def poly(t,x,y,z):
        return polynomial4(t,x,a,b,c,d,e)
    return poly
        
        

In [13]:
import numpy as np
t=0.
x=1.0
y=0.
z=0.0
print(t,x)
polyfn=polymaker(t,x,y,z,1.,0.,0.,0.,0.)
polyfn1=polymaker1(t,x,y,z,1,-1.0)

0.0 1.0


In [14]:
#import matplotlib.pyplot as plt
#plt.plot(t,polyfn(t,x))

In [15]:
rk4polyout=RK4(.01,t,x,y,z,polyfn1,True)
print(x)
print(outp+x)
print(rk4polyout)

-1.0
0.0 1.0 0.0 0.0 0.01
k1 -0.01
k2 -0.00995
k3 -0.00995025
k4 -0.0099004975
-0.00995016625
0.99004983375
1.0
2.0
(0.01, 0.99004983375)


In [16]:
dt=0.01
numsteps=10
intvals=[]
tvals=[]
for i in np.arange(1,numsteps):
    t,x=RK4(dt,t,x,y,z,polyfn1,True)
    #print(valueofintegral)
    intvals.append(x)
    tvals.append(t)
print(intvals)
print(tvals)

-1.0
0.0 1.0 0.0 0.0 0.01
k1 -0.01
k2 -0.00995
k3 -0.00995025
k4 -0.0099004975
-0.00995016625
0.99004983375
-0.99004983375
0.01 0.99004983375 0.0 0.0 0.01
k1 -0.0099004983375
k2 -0.009850995845812501
k3 -0.009851243358270938
k4 -0.009801985903917291
-0.00985116044159736
0.9801986733084026
-0.9801986733084026
0.02 0.9801986733084026 0.0 0.0 0.01
k1 -0.009801986733084026
k2 -0.009752976799418606
k3 -0.009753221849086932
k4 -0.009704454514593158
-0.009753139757448043
0.9704455335509545
-0.9704455335509545
0.03 0.9704455335509545 0.0 0.0 0.01
k1 -0.009704455335509546
k2 -0.009655933058831999
k3 -0.009656175670215386
k4 -0.009607893578807392
-0.009656094395401951
0.9607894391555526
-0.9607894391555526
0.04 0.9607894391555526 0.0 0.0 0.01
k1 -0.009607894391555526
k2 -0.009559854919597748
k3 -0.009560095116957538
k4 -0.009512293440385951
-0.009560014650842007
0.9512294245047106
-0.9512294245047106
0.05 0.9512294245047106 0.0 0.0 0.01
k1 -0.009512294245047107
k2 -0.00946473277382187
k3 -0.0094

RK4 is less precise than Euler for a 1st order polynomial RHS

RK4 is precise to 1 part in 10^3 and Euler is precise to 1 part in 10^6 for this equation. 

# Check precision for a fourth order polynomial of RK4 relative to Euler. RK4 should do better 

In [17]:
polyfn4=polymaker1(t,x,y,z,4,-1.0)

In [18]:
dt=0.01
numsteps=30
integralvals=[]
tvals=[]
t=1.
x=(3.)**(-1./3.)
print(x)
for i in np.arange(1,numsteps):
    t,x=RK4(dt,t,x,y,z,polyfn4,True)
    #print(valueofintegral)
    integralvals.append(x)
    tvals.append(t)
print(np.array(integralvals))
print(tvals)
print(len(integralvals),len(tvals))

0.6933612743506348
-0.231120424783545
1.0 0.6933612743506348 0.0 0.0 0.01
k1 -0.00231120424783545
k2 -0.0022958346968050985
k3 -0.0022959366507114584
k4 -0.0022807434751047346
-0.0022959150696622165
0.6910653592809726
-0.22807437600030617
1.01 0.6910653592809726 0.0 0.0 0.01
k1 -0.002280743760003062
k2 -0.002265726568170315
k3 -0.002265825203258446
k4 -0.0022509786648749128
-0.002265804327955916
0.6887995549530167
-0.2250978937754673
1.02 0.6887995549530167 0.0 0.0 0.01
k1 -0.002250978937754673
k2 -0.0022363026773626576
k3 -0.0022363981327168697
k4 -0.00222188704279087
-0.0022363779334507662
0.6865631770195659
-0.22218873042700318
1.03 0.6865631770195659 0.0 0.0 0.01
k1 -0.002221887304270032
k2 -0.0022075410247283976
k3 -0.0022076334323280346
k4 -0.002193447067092411
-0.002207613880912551
0.6843555631386534
-0.2193447317751573
1.04 0.6843555631386534 0.0 0.0 0.01
k1 -0.0021934473177515727
k2 -0.0021794205213487984
k3 -0.002179510006495144
k4 -0.0021656380836222533
-0.002179491076176951

In [19]:
x0=(3.)**(-1./3.)
x0

0.6933612743506348

The analyitic solution to the differential equation

dx/dt = -x^4 

is 

x= (3t)^(-1/3)

Below the output is shown. The results are plotted for scaling comparison. It doesn't look like it scales correctly. '

In [20]:
def ODEsolnanalytic(t):
    return (3.*t)**(-1./3.)

In [21]:
solnanalytic=[]
for i in np.arange(len(tvals)):
    solnanalytic.append(ODEsolnanalytic(tvals[i]))
print(np.array(solnanalytic))
print(len(solnanalytic))

[0.69106536 0.68879955 0.68656318 0.68435556 0.68217607 0.68002408
 0.67789899 0.67580022 0.6737272  0.67167939 0.66965624 0.66765726
 0.66568193 0.66372977 0.66180031 0.6598931  0.65800768 0.65614362
 0.65430051 0.65247794 0.65067551 0.64889282 0.64712952 0.64538523
 0.64365959 0.64195226 0.64026291 0.63859119 0.6369368 ]
29


In [22]:
dt=0.01
numsteps=30
xvals=[]
tvals=[]
for i in np.arange(1,numsteps):
    #t=0.+i*dt
    t,x=euler(dt,t,x,y,z,polyfn4,True)
    print(x)
    xvals.append(x)
    tvals.append(t)
print(xvals)
print(tvals)

0.01 1.2900000000000003 0.6369368049183575 -0.0016987409780349837 0.6352380639403225
0.6352380639403225
0.01 1.3000000000000003 0.6352380639403225 -0.0016808341379371133 0.6335572298023854
0.6335572298023854
0.01 1.3100000000000003 0.6335572298023854 -0.0016632557774400702 0.6318939740249453
0.6318939740249453
0.01 1.3200000000000003 0.6318939740249453 -0.0016459973424855106 0.6302479766824598
0.6302479766824598
0.01 1.3300000000000003 0.6302479766824598 -0.001629050566696136 0.6286189261157636
0.6286189261157636
0.01 1.3400000000000003 0.6286189261157636 -0.001612407459548534 0.6270065186562152
0.6270065186562152
0.01 1.3500000000000003 0.6270065186562152 -0.0015960602951194728 0.6254104583610957
0.6254104583610957
0.01 1.3600000000000003 0.6254104583610957 -0.0015800016013736567 0.623830456759722
0.623830456759722
0.01 1.3700000000000003 0.623830456759722 -0.0015642241499630072 0.622266232609759
0.622266232609759
0.01 1.3800000000000003 0.622266232609759 -0.0015487209465093541 0.6207

In [23]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(tvals,xvals, size=15, line_color="orange",fill_color="orange", fill_alpha=0.5, legend="Euler")
p.circle(tvals,integralvals, size=15, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="RK4")
p.circle(tvals,solnanalytic, size=15, line_color="green",fill_color="green", fill_alpha=0.5,legend="dx/dt=-x^4 exact")


p.circle(tvals,np.array(solnanalytic)-np.array(xvals),size=15, line_color="yellow",fill_color="yellow",fill_alpha=0.5, legend="abs diff Euler")
p.circle(tvals,np.array(solnanalytic)-np.array(integralvals),size=15, line_color="red", fill_color="red", fill_alpha=0.5,legend="abs diff RK4")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

This looks good to me. RK4 performs better on the 4th order RHS ODE than Euler does, they are both converging after initial transients, they both have small truncation error relative to their absolute value which improves with choice of time step, and the truncation error is worse for higher order functions. This seems very reasonable. 

# An equal mass system will be easier to obtain the necessary numerical precision than the Earth-Sun system. 

So start with two stellar mass objects in a binary. 

In [24]:
import math
def InitialDataEqualMass():
    phi=np.array([0,math.pi])
    orbitalangle=np.zeros(2)
    orbitalradius=100*np.ones(2)
    eccentricity=np.zeros(2)
    mass=np.ones(2)
    masssun=1.989*10**30
    lsun=3.828*10**26
    massearth=5.9722*10**24
    masses=mass #*masssun (natural units)
    return phi,orbitalangle,orbitalradius,eccentricity, masses
    

In [25]:
import random,numpy as np
initdateq=InitialDataEqualMass()

In [26]:
print(initdateq)

(array([0.        , 3.14159265]), array([0., 0.]), array([100., 100.]), array([0., 0.]), array([1., 1.]))


In [27]:
def getxyuveq(initdat): #using reduced mass cooordinate system
    phi,orbitangle,orbitalradius,eccentricity, masses=initdat
    #print(orbitalradius, phi, np.cos(phi), np.sin(phi))
    metersperAU=149597870700
    Gconstant=6.408*10**-11
    metersperAU=1
    Gconstant=1
    x0=orbitalradius*np.cos(phi)*metersperAU
    y0=orbitalradius*np.sin(phi)*metersperAU
    count=0
    for phi0 in phi:
        if phi0==0:
            print("zero")
            x0[count]=orbitalradius[count]
            y0[count]=0
        if phi0==math.pi:
            print("pi")
            x0[count]=-orbitalradius[count]
            y0[count]=0
        count+=1
    z0=np.zeros(2)
    print("x0", x0)
    print("y0", y0)
    
    #start at perihelion for both (eliptical, doesn't generalize to three body)
    #actually start with circular orbit
    ux0=np.zeros(2) #*149597870700
    #centrepital force balances gravitational force
    reducedmass=np.zeros(2)
    masstotal=np.sum(masses)
    reducedmass[0]=masstotal
    print(masses)
    for i in np.arange(1):
        j=(i+1)%2 #reverse masses
        reducedmass[i+1]=masses[i]*masses[j]/np.sum(masses)
    print(reducedmass)
    metersperAU=1 #natural units
    rphys=np.zeros(len(masses))
    for i in np.arange(2):
        rphys[i]=orbitalradius[i]*metersperAU*reducedmass[i]/masses[i]
    x0[0]=0.0
    x0phys=rphys*x0/orbitalradius
    x0phys[0]=0.0
    y0phys=rphys*y0/orbitalradius
    z0phys=np.zeros(2)
    r0=np.sqrt(x0**2+y0**2)
    print(rphys)
    #G=1
    Gconstant=1
    F=(Gconstant*masstotal**2/rphys**2)
    print(F)
    #centF=reducedmass*v**2/rphys
    #centF=accel
    v=np.sqrt(Gconstant*masstotal/rphys)
    print(v)
    print("r0", r0)
    ux0=-v*y0/orbitalradius[1]
    uy0=v*x0/orbitalradius[1]
        
    #ux0=-v*y0/r0
    #uy0=v*x0/r0 #initial data in y only
    #evolve in plane only
    #circular orbit
    uz0=np.zeros(2)
    
    a=Gconstant*masstotal/(rphys**2)
    ax0=-a*x0/orbitalradius[1]
    ay0=-a*y0/orbitalradius[1]
    az0=np.zeros(2)
    
    
    return masstotal, reducedmass,x0phys,y0phys,z0phys, ux0, uy0,uz0, ax0, ay0,az0

In [28]:
xyuvaeq=getxyuveq(initdateq)
print(xyuvaeq)#In natural units
print(xyuvaeq[2][0])
print(xyuvaeq[1][0]/xyuvaeq[1][1])
print(xyuvaeq)

zero
pi
x0 [ 100. -100.]
y0 [0. 0.]
[1. 1.]
[2.  0.5]
[200.  50.]
[0.0001 0.0016]
[0.1 0.2]
r0 [  0. 100.]
(2.0, array([2. , 0.5]), array([  0., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0. , -0.2]), array([0., 0.]), array([-0.    ,  0.0008]), array([-0., -0.]), array([0., 0.]))
0.0
4.0
(2.0, array([2. , 0.5]), array([  0., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0. , -0.2]), array([0., 0.]), array([-0.    ,  0.0008]), array([-0., -0.]), array([0., 0.]))


In [29]:
def timestep(step,t,dt,mtotal, reducedmass,xi,yi,zi, vxi, vyi, vzi, axi, ayi, azi):
    xii=np.zeros(np.size(xi))
    vxii=np.zeros(np.size(vxi))
    yii=np.zeros(np.size(yi))
    vyii=np.zeros(np.size(vyi))
    zii=np.zeros(np.size(vzi))
    vzii=np.zeros(np.size(vzi))
    rii=np.zeros(np.size(xi))
    axii=np.zeros(np.size(axi))
    ayii=np.zeros(np.size(ayi))
    azii=np.zeros(np.size(azi))
    
    #This is redundant in the center of mass system
    Gconstant=6.408*10**-11
    Gconstant=1
    for k in np.arange(len(rii)):
        for j in np.arange(1,len(rii)):
            if j==0:
                axii[j]=0.0
                ayii[j]=0.0
                azii[j]=0.0
            if j!=k:
                rreljk=np.abs((xi[j] - xi[k])**2+(yi[j]-yi[k])**2+(zi[j]-zi[k])**2)**(1./2.)
                axii[j]-=Gconstant*reducedmass[k]*(xi[j]  - xi[k])/rreljk**3
                ayii[j]-=Gconstant*reducedmass[k]*(yi[j]  - yi[k])/rreljk**3
                azii[j]-=Gconstant*reducedmass[k]*(zi[j]  - zi[k])/rreljk**3
    #print(xii)
    
    for m in np.arange(len(x)):
        #m represents choices of mass
        i=step
        
        xii[m] = xi[m] + dt*vxi[m]
        #print(xii)
        vxii[m] = vxi[m] + dt*axii[m]
        #print(vxii)
        yii[m]= yi[m] + dt*vyi[m]
        vyii[m] = vyi[m] + dt*ayii[m]
        zii[m]= zi[m] + dt*vzi[m]
        vzii[m] = vzi[m] + dt*azii[m]
        rii[m]=np.sqrt(xi[m]**2+yi[m]**2+zi[m]**2)
    
    
    
    return reducedmass, xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii
                    

In [30]:
dt=1 #*31556926 #seconds per year
numsteps=2000
masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeq
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
for i in np.arange(1,numsteps):
    t=0.+i*numsteps*dt
    mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
    print(x,y,vx,vy,ax,ay)
    #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
    #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
    #print(ax)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 

[  0. -50.] [ 0.  -0.2] [0.     0.0008] [ 0.  -0.2] [0.     0.0008] [0. 0.]
[  0.     -49.9992] [ 0.  -0.4] [0.         0.00159998] [ 0.        -0.1999968] [0.         0.00079998] [0.0000000e+00 3.1999232e-06]
[  0.         -49.99760002] [ 0.        -0.5999968] [0.         0.00239993] [ 0.        -0.1999904] [0.         0.00079995] [0.00000000e+00 6.39969281e-06]
[  0.         -49.99520009] [ 0.        -0.7999872] [0.         0.00319983] [ 0.        -0.1999808] [0.        0.0007999] [0.00000000e+00 9.59925762e-06]
[  0.         -49.99200026] [ 0.       -0.999968] [0.         0.00399968] [ 0.       -0.199968] [0.         0.00079985] [0.00000000e+00 1.27985664e-05]
[  0.         -49.98800058] [ 0.       -1.199936] [0.         0.00479946] [ 0.       -0.199952] [0.         0.00079978] [0.0000000e+00 1.5997568e-05]
[  0.         -49.98320112] [ 0.         -1.39988801] [0.         0.00559915] [ 0.         -0.19993281] [0.         0.00079969] [0.00000000e+00 1.91962112e-05]
[  0.         -49.

[  0.         -41.10038661] [  0.         -28.59940026] [0.         0.11417284] [ 0.         -0.16445165] [0.         0.00065662] [0.         0.00045302]
[  0.         -40.98621377] [  0.         -28.76385192] [0.         0.11482763] [ 0.         -0.16399602] [0.         0.00065479] [0.         0.00045563]
[  0.         -40.87138614] [  0.         -28.92784794] [0.         0.11548058] [ 0.         -0.16353779] [0.         0.00065295] [0.         0.00045823]
[  0.         -40.75590556] [  0.         -29.09138573] [0.         0.11613167] [ 0.         -0.16307696] [0.         0.00065109] [0.         0.00046083]
[  0.         -40.63977389] [  0.        -29.2544627] [0.        0.1167809] [ 0.         -0.16261355] [0.         0.00064923] [0.         0.00046342]
[  0.       -40.522993] [  0.         -29.41707625] [0.         0.11742825] [ 0.         -0.16214755] [0.         0.00064735] [0.       0.000466]
[  0.         -40.40556475] [  0.        -29.5792238] [0.         0.11807372] [ 0.      

[  0.         -15.60394308] [  0.        -47.7299747] [0.         0.18997549] [ 0.         -0.06297016] [0.         0.00024947] [0.         0.00075292]
[  0.         -15.41396759] [  0.         -47.79294486] [0.         0.19022194] [ 0.         -0.06221629] [0.         0.00024646] [0.         0.00075387]
[  0.         -15.22374565] [  0.         -47.85516115] [0.         0.19046538] [ 0.         -0.06146147] [0.         0.00024344] [0.         0.00075481]
[  0.         -15.03328027] [  0.         -47.91662262] [0.        0.1907058] [ 0.         -0.06070573] [0.         0.00024042] [0.         0.00075574]
[  0.         -14.84257447] [  0.         -47.97732836] [0.         0.19094319] [ 0.         -0.05994908] [0.         0.00023739] [0.         0.00075666]
[  0.         -14.65163127] [  0.         -48.03727744] [0.         0.19117756] [ 0.         -0.05919152] [0.         0.00023436] [0.         0.00075756]
[  0.         -14.46045372] [  0.         -48.09646896] [0.         0.19140889] 

[0.         6.10544799] [  0.         -50.00628393] [0.         0.19852928] [0.         0.02289659] [ 0.0000000e+00 -9.2409319e-05] [0.         0.00078267]
[0.         6.30397727] [  0.         -49.98338734] [0.         0.19843378] [0.         0.02367883] [ 0.00000000e+00 -9.55068471e-05] [0.         0.00078224]
[0.         6.50241105] [  0.         -49.95970851] [0.         0.19833517] [0.         0.02446064] [ 0.00000000e+00 -9.86022658e-05] [0.        0.0007818]
[0.         6.70074622] [  0.         -49.93524787] [0.         0.19823348] [0.         0.02524199] [ 0.        -0.0001017] [0.         0.00078135]
[0.        6.8989797] [  0.         -49.91000588] [0.         0.19812869] [0.         0.02602288] [ 0.         -0.00010479] [0.         0.00078089]
[0.         7.09710839] [  0.       -49.883983] [0.         0.19802082] [0.         0.02680329] [ 0.         -0.00010788] [0.         0.00078041]
[0.        7.2951292] [  0.         -49.85717971] [0.         0.19790985] [0.         0.

[ 0.         32.41702337] [  0.         -38.94846066] [0.         0.15428825] [0.         0.12588718] [ 0.         -0.00049594] [0.         0.00060065]
[ 0.         32.57131162] [  0.         -38.82257347] [0.      0.15379] [0.         0.12648582] [ 0.         -0.00049825] [0.         0.00059864]
[ 0.         32.72510162] [  0.         -38.69608765] [0.         0.15328944] [0.         0.12708245] [ 0.         -0.00050055] [0.         0.00059662]
[ 0.         32.87839106] [  0.        -38.5690052] [0.        0.1527866] [0.         0.12767704] [ 0.         -0.00050285] [0.        0.0005946]
[ 0.         33.03117766] [  0.         -38.44132816] [0.         0.15228146] [0.         0.12826961] [ 0.         -0.00050513] [0.         0.00059256]
[ 0.         33.18345912] [  0.         -38.31305855] [0.         0.15177405] [0.         0.12886013] [ 0.         -0.00050741] [0.         0.00059052]
[ 0.         33.33523317] [  0.         -38.18419842] [0.         0.15126437] [0.        0.1294486] 

...

[  0.         -20.73484038] [ 0.         48.04379669] [ 0.         -0.17922773] [ 0.         -0.07668674] [0.         0.00028694] [ 0.         -0.00067173]
[  0.         -20.91406811] [ 0.         47.96710995] [ 0.        -0.1789383] [ 0.         -0.07735737] [0.         0.00028943] [ 0.         -0.00067063]
[  0.         -21.09300641] [ 0.         47.88975258] [ 0.         -0.17864638] [ 0.         -0.07802689] [0.         0.00029192] [ 0.         -0.00066952]
[  0.         -21.27165279] [ 0.         47.81172569] [ 0.         -0.17835198] [ 0.        -0.0786953] [0.        0.0002944] [ 0.         -0.00066841]
[  0.         -21.45000477] [ 0.         47.73303038] [ 0.        -0.1780551] [ 0.         -0.07936258] [0.         0.00029688] [ 0.         -0.00066728]
[  0.         -21.62805987] [ 0.        47.6536678] [ 0.         -0.17775576] [ 0.         -0.08002873] [0.         0.00029935] [ 0.         -0.00066615]
[  0.         -21.80581563] [ 0.         47.57363907] [ 0.         -0.1774

[  0.         -44.82190969] [ 0.         27.21726881] [ 0.         -0.10124487] [ 0.         -0.16663364] [0.         0.00062029] [ 0.         -0.00037982]
[  0.         -44.92315456] [ 0.         27.05063517] [ 0.         -0.10062318] [ 0.         -0.16701115] [0.         0.00062169] [ 0.         -0.00037751]
[  0.         -45.02377774] [ 0.         26.88362403] [ 0.         -0.10000011] [ 0.         -0.16738633] [0.         0.00062308] [ 0.         -0.00037519]
[  0.         -45.12377785] [ 0.         26.71623769] [ 0.         -0.09937565] [ 0.        -0.1677592] [0.         0.00062446] [ 0.         -0.00037286]
[  0.        -45.2231535] [ 0.        26.5484785] [ 0.         -0.09874982] [ 0.         -0.16812973] [0.         0.00062583] [ 0.         -0.00037053]
[  0.         -45.32190332] [ 0.         26.38034876] [ 0.         -0.09812262] [ 0.         -0.16849793] [0.         0.00062719] [ 0.        -0.0003682]
[  0.         -45.42002594] [ 0.         26.21185084] [ 0.         -0.09

[  0.         -52.43046292] [ 0.         -2.39022647] [0.         0.00901528] [ 0.         -0.19502858] [0.         0.00072541] [0.00000000e+00 3.03668695e-05]
[  0.         -52.42144764] [ 0.         -2.58525505] [0.         0.00974057] [ 0.         -0.19499551] [0.         0.00072529] [0.00000000e+00 3.30647678e-05]
[  0.         -52.41170707] [ 0.         -2.78025056] [0.         0.01046572] [ 0.         -0.19495975] [0.         0.00072515] [0.00000000e+00 3.57621719e-05]
[  0.         -52.40124136] [ 0.         -2.97521031] [0.         0.01119073] [ 0.         -0.19492129] [0.         0.00072501] [0.00000000e+00 3.84590444e-05]
[  0.         -52.39005063] [ 0.         -3.17013161] [0.         0.01191558] [ 0.         -0.19488014] [0.         0.00072485] [0.00000000e+00 4.11553479e-05]
[  0.         -52.37813505] [ 0.         -3.36501174] [0.         0.01264027] [ 0.         -0.19483629] [0.         0.00072469] [0.0000000e+00 4.3851045e-05]
[  0.         -52.36549478] [ 0.         -

[  0.        -45.4358481] [  0.         -26.34928292] [0.         0.09801372] [ 0.         -0.16908851] [0.         0.00062851] [0.         0.00036137]
[  0.         -45.33783438] [  0.         -26.51837143] [0.         0.09864087] [ 0.         -0.16872481] [0.         0.00062715] [0.        0.0003637]
[  0.         -45.23919351] [  0.         -26.68709624] [0.         0.09926665] [ 0.         -0.16835879] [0.         0.00062578] [0.         0.00036602]
[  0.         -45.13992686] [  0.         -26.85545502] [0.         0.09989106] [ 0.         -0.16799044] [0.         0.00062441] [0.         0.00036834]
[  0.        -45.0400358] [  0.         -27.02344546] [0.         0.10051408] [ 0.         -0.16761978] [0.         0.00062302] [0.         0.00037066]
[  0.         -44.93952172] [  0.         -27.19106524] [0.         0.10113571] [ 0.         -0.16724681] [0.         0.00062163] [0.         0.00037297]
[  0.       -44.838386] [  0.         -27.35831205] [0.         0.10175594] [ 0.  

[  0.         -28.18160976] [  0.         -44.41180294] [0.         0.16484509] [ 0.         -0.10512044] [0.        0.0003896] [0.         0.00060896]
[  0.         -28.01676467] [  0.         -44.51692338] [0.         0.16523241] [ 0.         -0.10451005] [0.         0.00038732] [0.         0.00061039]
[  0.         -27.85153226] [  0.         -44.62143343] [0.         0.16561745] [ 0.         -0.10389825] [0.         0.00038504] [0.         0.00061181]
[  0.         -27.68591481] [  0.         -44.72533168] [0.        0.1660002] [ 0.         -0.10328503] [0.         0.00038275] [0.         0.00061321]
[  0.        -27.5199146] [  0.         -44.82861671] [0.         0.16638066] [ 0.         -0.10267042] [0.         0.00038046] [0.         0.00061461]
[  0.         -27.35353394] [  0.         -44.93128713] [0.         0.16675882] [ 0.         -0.10205442] [0.         0.00037816] [0.       0.000616]
[  0.         -27.18677512] [  0.         -45.03334155] [0.         0.16713468] [ 0.  

In [31]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="R0=100, Circular, Euler Method, Reduced Mass System", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1,ycoord1, size=15, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2,ycoord2, size=15, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

This is definitely an orbit! It is closer to closed when I go to R0=100 than at R0=1. Probably some of the reason it is not entirely closed and is losing energy is due to numerical artifacts as c->1 in Natural Units. Although this is Newtonian Gravity and not General Relativity, I do not really expect the computation to behave well in the limit c->1. 

# Check convergence with different step sizes

Euler is a first order method. The truncation error is theoretically proportional to the step size. Truncation error is error associated with the numerical approximation used to evaluate the differential equation mathematically in the code, rather than roundoff error inherrent to the mathematical limitations of the precision of the processor that accumulates over time. In this computation, we expect truncation error to dominate since Euler is a low precision approximation. To determine if the Euler method is working correctly, it is necessary to test the convergence of the Euler method and this orbital evolution code with the step size after one orbit. For this, I use the L^0 error, which is the absolute value of the x coordinate difference between the starting position (which is on the x axis) and the line interpolated through the nearest two points to either side of the x axis after one orbit.

In [32]:
def RunFirstOrbit(dt,initcondition,printoutput):
    masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=initcondition
    x0=x[1]
    lastvalue=[1,1]
    thisvalue=[x[1],y[1]]
    i=1
    while not (lastvalue[0]<0 and lastvalue[1]>0 and thisvalue[0]< 0 and thisvalue[1]<=0):
        t=0.+i*numsteps*dt
        mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
        if printoutput:
            print(x,y,vx,vy,ax,ay)
        #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
        #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
        #print(ax)
        xy=[x,y]
        xyt=np.transpose(xy)
        lastvalue,thisvalue=thisvalue, xyt[1]
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        if printoutput:
            print(x,y,lastvalue,thisvalue)
        i+=1
    
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay)
    return np.abs(x0-(thisvalue[0]+lastvalue[0])/2.)

In [33]:
dt=1 #*31556926 #seconds per year
numsteps=2000
masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeq
L0arrrm=[]
dtarrrm=[]
dtinit=0.125
for i in np.arange(8):
    dt=(2**i)*dtinit
    dtarrrm.append(dt)
    L0=RunFirstOrbit(dt,xyuvaeq,False)
    L0arrrm.append(L0)
print(dtarrrm, L0arrrm)

[0.125, 0.25, 0.5, 1.0, 2.0, 4.0, 8.0, 16.0] [0.31366360711112407, 0.6263414028992571, 1.248772740162181, 2.4818279915402215, 4.902225488705284, 9.564584346681642, 18.218283114348893, 33.10474126672807]


In [34]:
print(dtarrrm, L0arrrm)

[0.125, 0.25, 0.5, 1.0, 2.0, 4.0, 8.0, 16.0] [0.31366360711112407, 0.6263414028992571, 1.248772740162181, 2.4818279915402215, 4.902225488705284, 9.564584346681642, 18.218283114348893, 33.10474126672807]


In [35]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Euler method has linear truncation error, reduced mass", x_axis_label="dt", y_axis_label="L0 error", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(dtarrrm,L0arrrm, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")

p.legend.location = "top_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

Convergence of L0 truncation error of the Euler method with dt is linear as predicted. 

# Compare to the two body form without the reduced mass

This is a more complicated system where two body evolution is necessary, not just physically but computationally. 

In [36]:
def getxyuveqnocm(initdat):
    phi,orbitangle,orbitalradius,eccentricity, masses=initdat
    print("initdat", orbitalradius, phi, np.cos(phi), np.sin(phi))
    metersperAU=149597870700
    Gconstant=6.408*10**-11
    metersperAU=1
    Gconstant=1
    #fix x0 y0 at one star, disregard initial data, use orbital radius as separation between stars
    #this is consistant with choice in previous part
    cosphi=np.cos(phi)
    sinphi=np.sin(phi)
    coordsep=orbitalradius/2.
    print("coordsep",coordsep)
    #x0=orbitalradius/2.*np.cos(phi)*metersperAU
    #y0=orbitalradius/2.*np.sin(phi)*metersperAU
    count=0
    for phi0 in phi:
        if phi0==0:
            print("zero")
            #x0[count]=orbitalradius[count]/2.
            #y0[count]=0
            cosphi[count]=1.0
            sinphi[count]=0.0
        if phi0==math.pi:
            cosphi[count]=-1.0
            sinphi[count]=0.0
            print("pi")
            #x0[count]=-orbitalradius[count]/2.
            #y0[count]=0
        if phi0==math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=1.0
            #x0[count]=0
            #y0[count]=orbitalradius[count]/2.
        if phi0==3*math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=-1.0
            #x0[count]=0
            #y0[count]=-orbitalradius[count]/2.
        count+=1
    x0=coordsep*cosphi
    y0=coordsep*sinphi
    #x0[1]=0.0
    #y0[1]=0.0
    z0=np.zeros(2)
    print(x0)
    print(y0)
    
    #start at perihelion for both (eliptical, doesn't generalize to three body)
    #actually start with circular orbit
    ux0=np.zeros(2) #*149597870700
    #centrepital force balances gravitational force
    metersperAU=1 #natural units
    #G=1
    Gconstant=1
    #Fcentripital=mass1*v**2/rphys
    #centF=accel
    #Faccel=G*m1*m2/r^2
    r0=2.*orbitalradius #MYSTERY FACTOR OF TWO
    print("r0", r0)
    v=np.zeros(2)
    for i in np.arange(2):
        v[i]=np.sqrt(Gconstant*masses[(i+1)%2]/np.abs(r0[i]))
    print(v)
    #r0=orbitalradius #np.sqrt(x0**2+y0**2)
    ux0=-v*sinphi
    uy0=v*cosphi #initial data in y only 
    uz0=np.zeros(2)
    
    a=np.zeros(2)
    for i in np.arange(2):
        a[i]=Gconstant*masses[(i+1)%2]/(r0[i]**2)
    
    ax0=-a*cosphi
    ay0=-a*sinphi
    az0=np.zeros(2)
    
    
    return masses,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0

In [37]:
xyuvaeqnocm=getxyuveqnocm(initdateq)
print(xyuvaeqnocm)#In natural units
print(xyuvaeqnocm[1][0])
print(xyuvaeqnocm[0][0]/xyuvaeq[1][1])
print(xyuvaeqnocm)

initdat [100. 100.] [0.         3.14159265] [ 1. -1.] [0.0000000e+00 1.2246468e-16]
coordsep [50. 50.]
zero
pi
[ 50. -50.]
[0. 0.]
r0 [200. 200.]
[0.07071068 0.07071068]
(array([1., 1.]), array([ 50., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.07071068, -0.07071068]), array([0., 0.]), array([-2.5e-05,  2.5e-05]), array([-0., -0.]), array([0., 0.]))
50.0
2.0
(array([1., 1.]), array([ 50., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0.07071068, -0.07071068]), array([0., 0.]), array([-2.5e-05,  2.5e-05]), array([-0., -0.]), array([0., 0.]))


In [38]:
def timestep(step,t,dt,mtotal, mass,xi,yi,zi, vxi, vyi, vzi, axi, ayi, azi):
    xii=np.zeros(np.size(xi))
    vxii=np.zeros(np.size(vxi))
    yii=np.zeros(np.size(yi))
    vyii=np.zeros(np.size(vyi))
    zii=np.zeros(np.size(vzi))
    vzii=np.zeros(np.size(vzi))
    rii=np.zeros(np.size(xi))
    axii=np.zeros(np.size(axi))
    ayii=np.zeros(np.size(ayi))
    azii=np.zeros(np.size(azi))
    
    #This is redundant in the center of mass system
    Gconstant=6.408*10**-11
    Gconstant=1
    for k in np.arange(len(rii)):
        for j in np.arange(len(rii)):
            if j!=k:
                rreljk=np.abs((xi[j] - xi[k])**2+(yi[j]-yi[k])**2+(zi[j]-zi[k])**2)**(1./2.)
                #print(rreljk)
                axii[j]-=Gconstant*mass[k]*(xi[j]  - xi[k])/rreljk**3
                ayii[j]-=Gconstant*mass[k]*(yi[j]  - yi[k])/rreljk**3
                azii[j]-=Gconstant*mass[k]*(zi[j]  - zi[k])/rreljk**3
    #print(xii)
    
    for m in np.arange(len(x)):
        #m represents choices of mass
        i=step
        
        xii[m] = xi[m] + dt*vxi[m]
        vxii[m] = vxi[m] + dt*axi[m]
        yii[m]= yi[m] + dt*vyi[m]
        vyii[m] = vyi[m] + dt*ayi[m]
        zii[m]= zi[m] + dt*vzi[m]
        vzii[m] = vzi[m] + dt*azi[m]
        rii[m]=np.sqrt(xi[m]**2+yi[m]**2+zi[m]**2)
        
        #print(vyii[m],vyi[m],ayi[m],dt)
        #print(yii[m],yi[m],vyi[m],dt)
    
    
    return mass, xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii
                    

In [39]:
dt=1 #*31556926 #seconds per year
numsteps=10000
mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeqnocm
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
t=0.
masstotal=1. #DEFINE ME
for i in np.arange(1,numsteps):
    mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
    print(x,y,vx,vy,ax,ay)
    #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
    #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
    #print(ax)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 

[ 50. -50.] [ 0.07071068 -0.07071068] [-2.5e-05  2.5e-05] [ 0.07071068 -0.07071068] [-0.0001  0.0001] [0. 0.]
[ 49.999975 -49.999975] [ 0.14142136 -0.14142136] [-0.000125  0.000125] [ 0.07071068 -0.07071068] [-9.99997e-05  9.99997e-05] [-1.41420932e-07  1.41420932e-07]
[ 49.99985 -49.99985] [ 0.21213203 -0.21213203] [-0.000225  0.000225] [ 0.07071054 -0.07071054] [-9.99989e-05  9.99989e-05] [-2.82839743e-07  2.82839743e-07]
[ 49.999625 -49.999625] [ 0.28284257 -0.28284257] [-0.000325  0.000325] [ 0.07071025 -0.07071025] [-9.99979e-05  9.99979e-05] [-4.24256432e-07  4.24256432e-07]
[ 49.9993 -49.9993] [ 0.35355282 -0.35355282] [-0.000425  0.000425] [ 0.07070983 -0.07070983] [-9.99967001e-05  9.99967001e-05] [-5.65670717e-07  5.65670717e-07]
[ 49.99887501 -49.99887501] [ 0.42426265 -0.42426265] [-0.00052499  0.00052499] [ 0.07070926 -0.07070926] [-9.99953001e-05  9.99953001e-05] [-7.07082316e-07  7.07082316e-07]
[ 49.99835001 -49.99835001] [ 0.49497192 -0.49497192] [-0.00062499  0.000624

[ 49.76387857 -49.76387857] [ 4.94234264 -4.94234264] [-0.00691314  0.00691314] [ 0.07037925 -0.07037925] [-9.94901782e-05  9.94901782e-05] [-9.73889512e-06  9.73889512e-06]
[ 49.75696543 -49.75696543] [ 5.01272189 -5.01272189] [-0.00701263  0.00701263] [ 0.07036951 -0.07036951] [-9.94758047e-05  9.94758047e-05] [-9.87952558e-06  9.87952558e-06]
[ 49.7499528 -49.7499528] [ 5.0830914 -5.0830914] [-0.00711211  0.00711211] [ 0.07035963 -0.07035963] [-9.94612323e-05  9.94612323e-05] [-1.00201347e-05  1.00201347e-05]
[ 49.74284069 -49.74284069] [ 5.15345102 -5.15345102] [-0.00721157  0.00721157] [ 0.07034961 -0.07034961] [-9.9446461e-05  9.9446461e-05] [-1.01607222e-05  1.01607222e-05]
[ 49.73562913 -49.73562913] [ 5.22380063 -5.22380063] [-0.00731101  0.00731101] [ 0.07033945 -0.07033945] [-9.94314908e-05  9.94314908e-05] [-1.03012878e-05  1.03012878e-05]
[ 49.72831811 -49.72831811] [ 5.29414008 -5.29414008] [-0.00741045  0.00741045] [ 0.07032915 -0.07032915] [-9.94163218e-05  9.94163218e-

[ 48.64925411 -48.64925411] [ 11.63433571 -11.63433571] [-0.01637036  0.01637036] [ 0.06880702 -0.06880702] [-9.72088687e-05  9.72088687e-05] [-2.31019736e-05  2.31019736e-05]
[ 48.63288375 -48.63288375] [ 11.70314273 -11.70314273] [-0.01646757  0.01646757] [ 0.06878392 -0.06878392] [-9.71755925e-05  9.71755925e-05] [-2.32392765e-05  2.32392765e-05]
[ 48.61641619 -48.61641619] [ 11.77192664 -11.77192664] [-0.01656474  0.01656474] [ 0.06876068 -0.06876068] [-9.71421222e-05  9.71421222e-05] [-2.33765311e-05  2.33765311e-05]
[ 48.59985144 -48.59985144] [ 11.84068732 -11.84068732] [-0.01666188  0.01666188] [ 0.0687373 -0.0687373] [-9.71084577e-05  9.71084577e-05] [-2.35137373e-05  2.35137373e-05]
[ 48.58318956 -48.58318956] [ 11.90942463 -11.90942463] [-0.01675899  0.01675899] [ 0.06871379 -0.06871379] [-9.70745991e-05  9.70745991e-05] [-2.36508948e-05  2.36508948e-05]
[ 48.56643057 -48.56643057] [ 11.97813841 -11.97813841] [-0.01685607  0.01685607] [ 0.06869014 -0.06869014] [-9.70405465e-

[ 47.64850753 -47.64850753] [ 15.2460717 -15.2460717] [-0.02147204  0.02147204] [ 0.06739462 -0.06739462] [-9.51792973e-05  9.51792973e-05] [-3.03061978e-05  3.03061978e-05]
[ 47.62703549 -47.62703549] [ 15.31346632 -15.31346632] [-0.02156722  0.02156722] [ 0.06736432 -0.06736432] [-9.51358301e-05  9.51358301e-05] [-3.04405691e-05  3.04405691e-05]
[ 47.60546826 -47.60546826] [ 15.38083064 -15.38083064] [-0.02166236  0.02166236] [ 0.06733387 -0.06733387] [-9.50921729e-05  9.50921729e-05] [-3.05748777e-05  3.05748777e-05]
[ 47.5838059 -47.5838059] [ 15.44816451 -15.44816451] [-0.02175745  0.02175745] [ 0.0673033 -0.0673033] [-9.50483257e-05  9.50483257e-05] [-3.07091234e-05  3.07091234e-05]
[ 47.56204845 -47.56204845] [ 15.51546781 -15.51546781] [-0.0218525  0.0218525] [ 0.06727259 -0.06727259] [-9.50042885e-05  9.50042885e-05] [-3.08433058e-05  3.08433058e-05]
[ 47.54019595 -47.54019595] [ 15.5827404 -15.5827404] [-0.0219475  0.0219475] [ 0.06724175 -0.06724175] [-9.49600616e-05  9.4960

[ 45.54677306 -45.54677306] [ 20.7244701 -20.7244701] [-0.02920672  0.02920672] [ 0.06442819 -0.06442819] [-9.09335986e-05  9.09335986e-05] [-4.12210989e-05  4.12210989e-05]
[ 45.51756634 -45.51756634] [ 20.7888983 -20.7888983] [-0.02929765  0.02929765] [ 0.06438697 -0.06438697] [-9.0874694e-05  9.0874694e-05] [-4.13493592e-05  4.13493592e-05]
[ 45.48826869 -45.48826869] [ 20.85328527 -20.85328527] [-0.02938853  0.02938853] [ 0.06434562 -0.06434562] [-9.08156081e-05  9.08156081e-05] [-4.14775348e-05  4.14775348e-05]
[ 45.45888017 -45.45888017] [ 20.91763089 -20.91763089] [-0.02947934  0.02947934] [ 0.06430415 -0.06430415] [-9.0756341e-05  9.0756341e-05] [-4.16056254e-05  4.16056254e-05]
[ 45.42940083 -45.42940083] [ 20.98193504 -20.98193504] [-0.0295701  0.0295701] [ 0.06426254 -0.06426254] [-9.06968927e-05  9.06968927e-05] [-4.17336309e-05  4.17336309e-05]
[ 45.39983073 -45.39983073] [ 21.04619758 -21.04619758] [-0.0296608  0.0296608] [ 0.06422081 -0.06422081] [-9.06372634e-05  9.0637

...

[ 51.52750826 -51.52750826] [ 14.42699231 -14.42699231] [-0.01840422  0.01840422] [ 0.0658677 -0.0658677] [-8.41110198e-05  8.41110198e-05] [-2.34340375e-05  2.34340375e-05]
[ 51.50910404 -51.50910404] [ 14.49286001 -14.49286001] [-0.01848833  0.01848833] [ 0.06584427 -0.06584427] [-8.40807483e-05  8.40807483e-05] [-2.35414509e-05  2.35414509e-05]
[ 51.49061572 -51.49061572] [ 14.55870428 -14.55870428] [-0.01857241  0.01857241] [ 0.06582073 -0.06582073] [-8.40503393e-05  8.40503393e-05] [-2.36488253e-05  2.36488253e-05]
[ 51.47204331 -51.47204331] [ 14.62452501 -14.62452501] [-0.01865646  0.01865646] [ 0.06579708 -0.06579708] [-8.40197929e-05  8.40197929e-05] [-2.37561602e-05  2.37561602e-05]
[ 51.45338685 -51.45338685] [ 14.69032209 -14.69032209] [-0.01874048  0.01874048] [ 0.06577332 -0.06577332] [-8.39891091e-05  8.39891091e-05] [-2.38634557e-05  2.38634557e-05]
[ 51.43464637 -51.43464637] [ 14.75609541 -14.75609541] [-0.01882447  0.01882447] [ 0.06574946 -0.06574946] [-8.3958288e-0

[ 49.19599557 -49.19599557] [ 21.06945921 -21.06945921] [-0.02688456  0.02688456] [ 0.06289746 -0.06289746] [-8.02806376e-05  8.02806376e-05] [-3.42609001e-05  3.42609001e-05]
[ 49.16911101 -49.16911101] [ 21.13235667 -21.13235667] [-0.02696484  0.02696484] [ 0.0628632 -0.0628632] [-8.02365061e-05  8.02365061e-05] [-3.43633618e-05  3.43633618e-05]
[ 49.14214617 -49.14214617] [ 21.19521987 -21.19521987] [-0.02704508  0.02704508] [ 0.06282883 -0.06282883] [-8.01922435e-05  8.01922435e-05] [-3.44657663e-05  3.44657663e-05]
[ 49.11510109 -49.11510109] [ 21.2580487 -21.2580487] [-0.02712527  0.02712527] [ 0.06279437 -0.06279437] [-8.01478497e-05  8.01478497e-05] [-3.45681137e-05  3.45681137e-05]
[ 49.08797582 -49.08797582] [ 21.32084307 -21.32084307] [-0.02720542  0.02720542] [ 0.0627598 -0.0627598] [-8.01033249e-05  8.01033249e-05] [-3.46704037e-05  3.46704037e-05]
[ 49.06077041 -49.06077041] [ 21.38360287 -21.38360287] [-0.02728552  0.02728552] [ 0.06272513 -0.06272513] [-8.00586691e-05  

[ 45.94367705 -45.94367705] [ 27.46770921 -27.46770921] [-0.03504885  0.03504885] [ 0.05875212 -0.05875212] [-7.49453227e-05  7.49453227e-05] [-4.46765999e-05  4.46765999e-05]
[ 45.9086282 -45.9086282] [ 27.52646132 -27.52646132] [-0.03512379  0.03512379] [ 0.05870744 -0.05870744] [-7.4887857e-05  7.4887857e-05] [-4.47721648e-05  4.47721648e-05]
[ 45.87350441 -45.87350441] [ 27.58516876 -27.58516876] [-0.03519868  0.03519868] [ 0.05866267 -0.05866267] [-7.48302691e-05  7.48302691e-05] [-4.48676553e-05  4.48676553e-05]
[ 45.83830573 -45.83830573] [ 27.64383143 -27.64383143] [-0.03527351  0.03527351] [ 0.0586178 -0.0586178] [-7.47725589e-05  7.47725589e-05] [-4.49630714e-05  4.49630714e-05]
[ 45.80303221 -45.80303221] [ 27.70244923 -27.70244923] [-0.03534828  0.03534828] [ 0.05857284 -0.05857284] [-7.47147266e-05  7.47147266e-05] [-4.50584129e-05  4.50584129e-05]
[ 45.76768393 -45.76768393] [ 27.76102207 -27.76102207] [-0.035423  0.035423] [ 0.05852778 -0.05852778] [-7.46567722e-05  7.46

[ 42.70289047 -42.70289047] [ 32.29286034 -32.29286034] [-0.04120217  0.04120217] [ 0.05462109 -0.05462109] [-6.96339573e-05  6.96339573e-05] [-5.25189809e-05  5.25189809e-05]
[ 42.6616883 -42.6616883] [ 32.34748143 -32.34748143] [-0.0412718  0.0412718] [ 0.05456858 -0.05456858] [-6.95664574e-05  6.95664574e-05] [-5.26076775e-05  5.26076775e-05]
[ 42.6204165 -42.6204165] [ 32.40205001 -32.40205001] [-0.04134137  0.04134137] [ 0.05451597 -0.05451597] [-6.9498844e-05  6.9498844e-05] [-5.26962869e-05  5.26962869e-05]
[ 42.57907513 -42.57907513] [ 32.45656598 -32.45656598] [-0.04141087  0.04141087] [ 0.05446327 -0.05446327] [-6.94311172e-05  6.94311172e-05] [-5.27848087e-05  5.27848087e-05]
[ 42.53766426 -42.53766426] [ 32.51102925 -32.51102925] [-0.0414803  0.0414803] [ 0.05441049 -0.05441049] [-6.93632773e-05  6.93632773e-05] [-5.2873243e-05  5.2873243e-05]
[ 42.49618396 -42.49618396] [ 32.56543973 -32.56543973] [-0.04154966  0.04154966] [ 0.05435761 -0.05435761] [-6.92953243e-05  6.9295

[ 38.58227915 -38.58227915] [ 37.13669855 -37.13669855] [-0.04737498  0.04737498] [ 0.04936914 -0.04936914] [-6.28864505e-05  6.28864505e-05] [-6.0375651e-05  6.0375651e-05]
[ 38.53490417 -38.53490417] [ 37.18606769 -37.18606769] [-0.04743787  0.04743787] [ 0.04930876 -0.04930876] [-6.28089106e-05  6.28089106e-05] [-6.04556192e-05  6.04556192e-05]
[ 38.4874663 -38.4874663] [ 37.23537645 -37.23537645] [-0.04750068  0.04750068] [ 0.0492483 -0.0492483] [-6.27312686e-05  6.27312686e-05] [-6.05354872e-05  6.05354872e-05]
[ 38.43996563 -38.43996563] [ 37.28462475 -37.28462475] [-0.04756341  0.04756341] [ 0.04918777 -0.04918777] [-6.26535246e-05  6.26535246e-05] [-6.06152547e-05  6.06152547e-05]
[ 38.39240222 -38.39240222] [ 37.33381252 -37.33381252] [-0.04762606  0.04762606] [ 0.04912715 -0.04912715] [-6.25756788e-05  6.25756788e-05] [-6.06949217e-05  6.06949217e-05]
[ 38.34477615 -38.34477615] [ 37.38293967 -37.38293967] [-0.04768864  0.04768864] [ 0.04906646 -0.04906646] [-6.24977313e-05  

In [40]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="dt=1, Euler Method, Equal Mass System", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1,ycoord1, size=1, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2,ycoord2, size=1, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

Beautiful circular orbit (with a mystery fudge factor of 2 in the initial conditions). There is a slight loss of energy with dt=1. Time to test the convergence with dt (keeping dt<1). 

Mystery factor of 2 comes from ambiguity in definition of orbital radius. 

In the reduced mass system, a coordinate transformation takes place that converts the system to two masses, one of which is equal to m1+m2 and is held fixed at the center of mass. The other of which is equal to mu=m1*m2/(m1+m2) and orbits about the heavier mass at a radius of rcm=r*mu/(m1+m2)

In the system with two equal masses, the center of mass is chosen as the center of the coordinate system, again, but no transformation is made to adjust the MASSES or the ORBITAL DYNAMICS of the stars. The two stars evolve around the mutual center of mass in two circles rather than one. The orbital radius r1=r2=1/2*r where r is the separation between the two. The ambiguity between r1, r, and rcm is where the mystery factor of 2 arises. I am going to leave it be for now since it is working and fix it when I generalize the initial conditions to work for more general orbits. 

In [41]:
def RunFirstOrbit2(dt,initcondition,printoutput):
    mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=initcondition
    x0=x[1]
    lastvalue=[1,1]
    thisvalue=[x[1],y[1]]
    i=1
    while not (lastvalue[0]<0 and lastvalue[1]>0 and thisvalue[0]< 0 and thisvalue[1]<=0):
        t=0.+i*numsteps*dt
        mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
        if printoutput:
            print(x,y,vx,vy,ax,ay)
        #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
        #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
        #print(ax)
        xy=[x,y]
        xyt=np.transpose(xy)
        lastvalue,thisvalue=thisvalue, xyt[1]
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        if printoutput:
            print(x,y,lastvalue,thisvalue)
        i+=1
    
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay) 
    #mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
    #print(x,y,vx,vy,ax,ay)
    return np.abs(x0-(thisvalue[0]+lastvalue[0])/2.)

In [42]:
dt=1 #*31556926 #seconds per year
numsteps=2000
mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeqnocm
L0arr=[]
dtarr=[]
dtinit=0.125/4.
for i in np.arange(6):
    dt=(2**i)*dtinit
    dtarr.append(dt)
    L0=RunFirstOrbit2(dt,xyuvaeqnocm,False)
    L0arr.append(L0)
print(dtarr, L0arr)

[0.03125, 0.0625, 0.125, 0.25, 0.5, 1.0] [0.05552050552522303, 0.11101002010160244, 0.22189608443575537, 0.4432999707941505, 0.8846192184580843, 1.7614318104975268]


In [43]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Euler method has linear truncation error, equal mass", x_axis_label="dt", y_axis_label="L0 error", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(dtarr,L0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")

p.legend.location = "top_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

# Try initial condition at 30 degrees to y axis with circular motion 

In [44]:
import math
def InitialDataEqualMass30degrees():
    phi=np.array([math.pi/6,7*math.pi/6])
    orbitalangle=np.zeros(2)
    orbitalradius=100*np.ones(2)
    eccentricity=np.zeros(2)
    mass=np.ones(2)
    masses=mass #*masssun (natural units)
    return phi,orbitalangle,orbitalradius,eccentricity, masses
    

In [45]:
import random,numpy as np
initdateq30degrees=InitialDataEqualMass30degrees()

In [46]:
xyuvaeq30degrees=getxyuveqnocm(initdateq30degrees)
print(xyuvaeq30degrees)

initdat [100. 100.] [0.52359878 3.66519143] [ 0.8660254 -0.8660254] [ 0.5 -0.5]
coordsep [50. 50.]
[ 43.30127019 -43.30127019]
[ 25. -25.]
r0 [200. 200.]
[0.07071068 0.07071068]
(array([1., 1.]), array([ 43.30127019, -43.30127019]), array([ 25., -25.]), array([0., 0.]), array([-0.03535534,  0.03535534]), array([ 0.06123724, -0.06123724]), array([0., 0.]), array([-2.16506351e-05,  2.16506351e-05]), array([-1.25e-05,  1.25e-05]), array([0., 0.]))


In [47]:
dt=1 #*31556926 #seconds per year
numsteps=10000
mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeq30degrees
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
for i in np.arange(1,numsteps):
    mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
    print(x,y,vx,vy,ax,ay)
    #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
    #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
    #print(ax)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 

[ 43.26591485 -43.26591485] [ 25.06123724 -25.06123724] [-0.03537699  0.03537699] [ 0.06122474 -0.06122474] [-8.66025404e-05  8.66025404e-05] [-5.e-05  5.e-05]
[ 43.23053786 -43.23053786] [ 25.12246199 -25.12246199] [-0.03546359  0.03546359] [ 0.06117474 -0.06117474] [-8.65315701e-05  8.65315701e-05] [-5.01223241e-05  5.01223241e-05]
[ 43.19507427 -43.19507427] [ 25.18363673 -25.18363673] [-0.03555012  0.03555012] [ 0.06112462 -0.06112462] [-8.64601679e-05  8.64601679e-05] [-5.02443964e-05  5.02443964e-05]
[ 43.15952414 -43.15952414] [ 25.24476135 -25.24476135] [-0.03563658  0.03563658] [ 0.06107438 -0.06107438] [-8.63885935e-05  8.63885935e-05] [-5.03663669e-05  5.03663669e-05]
[ 43.12388756 -43.12388756] [ 25.30583573 -25.30583573] [-0.03572297  0.03572297] [ 0.06102401 -0.06102401] [-8.63168472e-05  8.63168472e-05] [-5.04882352e-05  5.04882352e-05]
[ 43.08816459 -43.08816459] [ 25.36685974 -25.36685974] [-0.03580929  0.03580929] [ 0.06097352 -0.06097352] [-8.6244929e-05  8.6244929e-

[ 40.29392757 -40.29392757] [ 29.6204473 -29.6204473] [-0.04182458  0.04182458] [ 0.05702501 -0.05702501] [-8.06249545e-05  8.06249545e-05] [-5.9092727e-05  5.9092727e-05]
[ 40.25210298 -40.25210298] [ 29.67747231 -29.67747231] [-0.04190521  0.04190521] [ 0.05696592 -0.05696592] [-8.05409034e-05  8.05409034e-05] [-5.920638e-05  5.920638e-05]
[ 40.21019777 -40.21019777] [ 29.73443822 -29.73443822] [-0.04198575  0.04198575] [ 0.05690671 -0.05690671] [-8.04566921e-05  8.04566921e-05] [-5.93199131e-05  5.93199131e-05]
[ 40.16821202 -40.16821202] [ 29.79134493 -29.79134493] [-0.04206621  0.04206621] [ 0.05684739 -0.05684739] [-8.03723206e-05  8.03723206e-05] [-5.94333263e-05  5.94333263e-05]
[ 40.12614581 -40.12614581] [ 29.84819232 -29.84819232] [-0.04214658  0.04214658] [ 0.05678796 -0.05678796] [-8.02877893e-05  8.02877893e-05] [-5.95466192e-05  5.95466192e-05]
[ 40.08399923 -40.08399923] [ 29.90498028 -29.90498028] [-0.04222687  0.04222687] [ 0.05672841 -0.05672841] [-8.02030982e-05  8.

[ 35.32902025 -35.32902025] [ 35.41517424 -35.41517424] [-0.05001466  0.05001466] [ 0.05001195 -0.05001195] [-7.06578185e-05  7.06578185e-05] [-7.06301129e-05  7.06301129e-05]
[ 35.27900559 -35.27900559] [ 35.46518619 -35.46518619] [-0.05008532  0.05008532] [ 0.04994132 -0.04994132] [-7.05575044e-05  7.05575044e-05] [-7.07295673e-05  7.07295673e-05]
[ 35.22892027 -35.22892027] [ 35.51512751 -35.51512751] [-0.05015588  0.05015588] [ 0.04987059 -0.04987059] [-7.04570503e-05  7.04570503e-05] [-7.08288787e-05  7.08288787e-05]
[ 35.17876439 -35.17876439] [ 35.5649981 -35.5649981] [-0.05022633  0.05022633] [ 0.04979976 -0.04979976] [-7.03564562e-05  7.03564562e-05] [-7.09280471e-05  7.09280471e-05]
[ 35.12853806 -35.12853806] [ 35.61479786 -35.61479786] [-0.05029669  0.05029669] [ 0.04972883 -0.04972883] [-7.02557225e-05  7.02557225e-05] [-7.10270721e-05  7.10270721e-05]
[ 35.07824137 -35.07824137] [ 35.6645267 -35.6645267] [-0.05036695  0.05036695] [ 0.04965781 -0.04965781] [-7.01548492e-05

[ 32.95676038 -32.95676038] [ 37.64113565 -37.64113565] [-0.053159  0.053159] [ 0.04666223 -0.04666223] [-6.59014752e-05  6.59014752e-05] [-7.50541449e-05  7.50541449e-05]
[ 32.90360138 -32.90360138] [ 37.68779788 -37.68779788] [-0.0532249  0.0532249] [ 0.04658718 -0.04658718] [-6.579493e-05  6.579493e-05] [-7.51468244e-05  7.51468244e-05]
[ 32.85037647 -32.85037647] [ 37.73438505 -37.73438505] [-0.0532907  0.0532907] [ 0.04651203 -0.04651203] [-6.56882544e-05  6.56882544e-05] [-7.52393522e-05  7.52393522e-05]
[ 32.79708577 -32.79708577] [ 37.78089708 -37.78089708] [-0.05335639  0.05335639] [ 0.04643679 -0.04643679] [-6.55814484e-05  6.55814484e-05] [-7.53317281e-05  7.53317281e-05]
[ 32.74372939 -32.74372939] [ 37.82733387 -37.82733387] [-0.05342197  0.05342197] [ 0.04636146 -0.04636146] [-6.54745124e-05  6.54745124e-05] [-7.54239518e-05  7.54239518e-05]
[ 32.69030742 -32.69030742] [ 37.87369533 -37.87369533] [-0.05348744  0.05348744] [ 0.04628603 -0.04628603] [-6.53674466e-05  6.5367

[ 26.97634507 -26.97634507] [ 42.15254826 -42.15254826] [-0.05952756  0.05952756] [ 0.0382209 -0.0382209] [-5.39245186e-05  5.39245186e-05] [-8.39993173e-05  8.39993173e-05]
[ 26.91681751 -26.91681751] [ 42.19076916 -42.19076916] [-0.05958149  0.05958149] [ 0.0381369 -0.0381369] [-5.38053947e-05  5.38053947e-05] [-8.40749365e-05  8.40749365e-05]
[ 26.85723602 -26.85723602] [ 42.22890606 -42.22890606] [-0.05963529  0.05963529] [ 0.03805283 -0.03805283] [-5.36861647e-05  5.36861647e-05] [-8.41503859e-05  8.41503859e-05]
[ 26.79760073 -26.79760073] [ 42.26695889 -42.26695889] [-0.05968898  0.05968898] [ 0.03796867 -0.03796867] [-5.35668287e-05  5.35668287e-05] [-8.42256655e-05  8.42256655e-05]
[ 26.73791176 -26.73791176] [ 42.30492756 -42.30492756] [-0.05974254  0.05974254] [ 0.03788445 -0.03788445] [-5.34473871e-05  5.34473871e-05] [-8.43007752e-05  8.43007752e-05]
[ 26.67816921 -26.67816921] [ 42.34281201 -42.34281201] [-0.05979599  0.05979599] [ 0.03780015 -0.03780015] [-5.33278401e-05

...

[ 45.57194079 -45.57194079] [ 28.01621303 -28.01621303] [-0.03578198  0.03578198] [ 0.05825399 -0.05825399] [-7.44802219e-05  7.44802219e-05] [-4.56570703e-05  4.56570703e-05]
[ 45.53615881 -45.53615881] [ 28.07446702 -28.07446702] [-0.03585646  0.03585646] [ 0.05820833 -0.05820833] [-7.44216177e-05  7.44216177e-05] [-4.57520979e-05  4.57520979e-05]
[ 45.50030236 -45.50030236] [ 28.13267535 -28.13267535] [-0.03593088  0.03593088] [ 0.05816258 -0.05816258] [-7.43628922e-05  7.43628922e-05] [-4.58470503e-05  4.58470503e-05]
[ 45.46437148 -45.46437148] [ 28.19083793 -28.19083793] [-0.03600524  0.03600524] [ 0.05811673 -0.05811673] [-7.43040454e-05  7.43040454e-05] [-4.59419274e-05  4.59419274e-05]
[ 45.42836624 -45.42836624] [ 28.24895467 -28.24895467] [-0.03607955  0.03607955] [ 0.05807079 -0.05807079] [-7.42450776e-05  7.42450776e-05] [-4.6036729e-05  4.6036729e-05]
[ 45.39228669 -45.39228669] [ 28.30702546 -28.30702546] [-0.03615379  0.03615379] [ 0.05802476 -0.05802476] [-7.41859887e-

[ 39.9113407 -39.9113407] [ 35.6351808 -35.6351808] [-0.04552102  0.04552102] [ 0.05103145 -0.05103145] [-6.5215416e-05  6.5215416e-05] [-5.80785131e-05  5.80785131e-05]
[ 39.86581968 -39.86581968] [ 35.68621225 -35.68621225] [-0.04558624  0.04558624] [ 0.05097337 -0.05097337] [-6.51409495e-05  6.51409495e-05] [-5.81616521e-05  5.81616521e-05]
[ 39.82023344 -39.82023344] [ 35.73718562 -35.73718562] [-0.04565138  0.04565138] [ 0.0509152 -0.0509152] [-6.50663767e-05  6.50663767e-05] [-5.82446956e-05  5.82446956e-05]
[ 39.77458207 -39.77458207] [ 35.78810082 -35.78810082] [-0.04571644  0.04571644] [ 0.05085696 -0.05085696] [-6.49916979e-05  6.49916979e-05] [-5.83276433e-05  5.83276433e-05]
[ 39.72886562 -39.72886562] [ 35.83895778 -35.83895778] [-0.04578143  0.04578143] [ 0.05079863 -0.05079863] [-6.49169131e-05  6.49169131e-05] [-5.84104951e-05  5.84104951e-05]
[ 39.68308419 -39.68308419] [ 35.88975641 -35.88975641] [-0.04584635  0.04584635] [ 0.05074022 -0.05074022] [-6.48420225e-05  6.

[ 33.10007638 -33.10007638] [ 42.05196829 -42.05196829] [-0.05371906  0.05371906] [ 0.04234211 -0.04234211] [-5.40778055e-05  5.40778055e-05] [-6.85227249e-05  6.85227249e-05]
[ 33.04635732 -33.04635732] [ 42.0943104 -42.0943104] [-0.05377314  0.05377314] [ 0.04227359 -0.04227359] [-5.39900003e-05  5.39900003e-05] [-6.85915571e-05  6.85915571e-05]
[ 32.99258418 -32.99258418] [ 42.13658398 -42.13658398] [-0.05382713  0.05382713] [ 0.04220499 -0.04220499] [-5.39021072e-05  5.39021072e-05] [-6.86602765e-05  6.86602765e-05]
[ 32.93875705 -32.93875705] [ 42.17878898 -42.17878898] [-0.05388103  0.05388103] [ 0.04213633 -0.04213633] [-5.38141263e-05  5.38141263e-05] [-6.87288829e-05  6.87288829e-05]
[ 32.88487602 -32.88487602] [ 42.22092531 -42.22092531] [-0.05393485  0.05393485] [ 0.04206761 -0.04206761] [-5.37260579e-05  5.37260579e-05] [-6.87973762e-05  6.87973762e-05]
[ 32.83094117 -32.83094117] [ 42.26299292 -42.26299292] [-0.05398857  0.05398857] [ 0.04199881 -0.04199881] [-5.3637902e-0

[ 25.45534059 -25.45534059] [ 47.08970267 -47.08970267] [-0.06015052  0.06015052] [ 0.03259235 -0.03259235] [-4.15876864e-05  4.15876864e-05] [-7.66983613e-05  7.66983613e-05]
[ 25.39519007 -25.39519007] [ 47.12229502 -47.12229502] [-0.0601921  0.0601921] [ 0.03251565 -0.03251565] [-4.14894567e-05  4.14894567e-05] [-7.6751131e-05  7.6751131e-05]
[ 25.33499797 -25.33499797] [ 47.15481067 -47.15481067] [-0.06023359  0.06023359] [ 0.0324389 -0.0324389] [-4.13911599e-05  4.13911599e-05] [-7.68037744e-05  7.68037744e-05]
[ 25.27476438 -25.27476438] [ 47.18724957 -47.18724957] [-0.06027498  0.06027498] [ 0.0323621 -0.0323621] [-4.12927961e-05  4.12927961e-05] [-7.68562913e-05  7.68562913e-05]
[ 25.21448939 -25.21448939] [ 47.21961167 -47.21961167] [-0.06031628  0.06031628] [ 0.03228524 -0.03228524] [-4.11943655e-05  4.11943655e-05] [-7.69086817e-05  7.69086817e-05]
[ 25.15417311 -25.15417311] [ 47.2518969 -47.2518969] [-0.06035747  0.06035747] [ 0.03220833 -0.03220833] [-4.10958683e-05  4.10

[ 17.32291873 -17.32291873] [ 50.66617255 -50.66617255] [-0.06471112  0.06471112] [ 0.02222523 -0.02222523] [-2.83144851e-05  2.83144851e-05] [-8.24699693e-05  8.24699693e-05]
[ 17.2582076 -17.2582076] [ 50.68839778 -50.68839778] [-0.06473944  0.06473944] [ 0.02214276 -0.02214276] [-2.82089351e-05  2.82089351e-05] [-8.25056561e-05  8.25056561e-05]
[ 17.19346816 -17.19346816] [ 50.71054054 -50.71054054] [-0.06476765  0.06476765] [ 0.02206026 -0.02206026] [-2.81033402e-05  2.81033402e-05] [-8.2541207e-05  8.2541207e-05]
[ 17.12870052 -17.12870052] [ 50.7326008 -50.7326008] [-0.06479575  0.06479575] [ 0.02197771 -0.02197771] [-2.79977004e-05  2.79977004e-05] [-8.25766219e-05  8.25766219e-05]
[ 17.06390477 -17.06390477] [ 50.75457851 -50.75457851] [-0.06482375  0.06482375] [ 0.02189514 -0.02189514] [-2.78920159e-05  2.78920159e-05] [-8.26119009e-05  8.26119009e-05]
[ 16.99908102 -16.99908102] [ 50.77647365 -50.77647365] [-0.06485164  0.06485164] [ 0.02181253 -0.02181253] [-2.7786287e-05  2

In [48]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Circular orbit, 30 degree init, Euler Method, Equal Mass", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1[:3000],ycoord1[:3000], size=1, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2[:3000],ycoord2[:3000], size=1, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

30 degree offset in initial conditions works beautifully! Circular orbits are clearly working. The next steps are to track down the reasons for the mystery factor of 2 in the initial conditions and to implement elliptical, hyperbolic, and parabolic orbit initial conditions. 

# Two body circular orbit equal mass again, using RK4, reduced mass system

In [49]:
import math
def InitialDataReducedMass(orbitalangle,r0):
    phi=orbitalangle
    radiusseparation=r0 #separation one hundred
    eccentricity=np.zeros(2)
    mass=np.ones(2)
    masssun=1.989*10**30
    lsun=3.828*10**26
    massearth=5.9722*10**24
    masses=mass #*masssun (natural units)
    return phi, radiusseparation,eccentricity, masses
    

In [50]:
def getxyuveqreducedmass(initdat): #using reduced mass cooordinate system
    phi,radiusseparation,eccentricity, masses=initdatreducedmass
    #print(orbitalradius, phi, np.cos(phi), np.sin(phi))
    metersperAU=1
    Gconstant=1
    x0=np.zeros(2)
    y0=np.zeros(2)
    x0[1]=radiusseparation*np.cos(phi)*metersperAU
    y0[1]=radiusseparation*np.sin(phi)*metersperAU
    if phi==0:
        print("zero")
        x0[1]=radiusseparation
        y0[1]=0
    if phi==math.pi:
        print("pi")
        x0[1]=-radiusseparation
        y0[1]=0
    z0=np.zeros(2)
    print("x0", x0)
    print("y0", y0)
    
    #start at perihelion for both (eliptical, doesn't generalize to three body)
    #actually start with circular orbit
    ux0=np.zeros(2) #*149597870700
    #centrepital force balances gravitational force
    reducedmass=np.zeros(2)
    masstotal=np.sum(masses)
    reducedmass[0]=masstotal
    print(masses)
    for i in np.arange(1):
        j=(i+1)%2 #reverse masses
        reducedmass[i+1]=masses[i]*masses[j]/np.sum(masses)
    print(reducedmass)
    metersperAU=1 #natural units
    rphys=np.zeros(len(masses))
    for i in np.arange(2):
        #rphys is r in the reduced mass system
        rphys[i]=radiusseparation #*metersperAU*reducedmass[i]/masses[i]
    x0[0]=0.0
    x0phys=rphys*x0/radiusseparation
    x0phys[0]=0.0
    y0phys=rphys*y0/radiusseparation
    z0phys=np.zeros(2)
    r0=np.sqrt(x0**2+y0**2)
    print(rphys)
    #G=1
    Gconstant=1
    F=(Gconstant*masstotal**2/(2*rphys)**2)
    print(F)
    #centF=reducedmass*v**2/rphys
    #centF=accel
    v=np.sqrt(Gconstant*masstotal/(rphys))
    print(v)
    print("r0", r0)
    ux0=-v*y0/radiusseparation #[1]
    uy0=v*x0/radiusseparation #[1]
        
    #ux0=-v*y0/r0
    #uy0=v*x0/r0 #initial data in y only
    #evolve in plane only
    #circular orbit
    uz0=np.zeros(2)
    
    a=Gconstant*masstotal/((2*rphys)**2)
    ax0=-a*x0/radiusseparation
    ay0=-a*y0/radiusseparation
    az0=np.zeros(2)
    
    
    return masstotal, reducedmass,x0phys,y0phys,z0phys, ux0, uy0,uz0, ax0, ay0,az0

In [51]:
import random,numpy as np
initdatreducedmass=InitialDataReducedMass(0,50)

In [52]:
xyuvaeqreducedmass=getxyuveqreducedmass(initdateq)
print(xyuvaeq)#In natural units
print(xyuvaeq[2][0])
print(xyuvaeq[1][0]/xyuvaeq[1][1])
print(xyuvaeq)

zero
x0 [ 0. 50.]
y0 [0. 0.]
[1. 1.]
[2.  0.5]
[50. 50.]
[0.0004 0.0004]
[0.2 0.2]
r0 [ 0. 50.]
(2.0, array([2. , 0.5]), array([  0., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0. , -0.2]), array([0., 0.]), array([-0.    ,  0.0008]), array([-0., -0.]), array([0., 0.]))
0.0
4.0
(2.0, array([2. , 0.5]), array([  0., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0. , -0.2]), array([0., 0.]), array([-0.    ,  0.0008]), array([-0., -0.]), array([0., 0.]))


In [53]:
def RK4implicit(h,t,x,f): #not a finite difference so no step in y
    k1= h*f(t)
    k2=h*f(t+h/2.)
    k3=h*f(t+h/2.)
    k4=h*f(t+h)
    return t+h, x+1/6.*(k1+2.*k2+2.*k3+k4)




In [54]:
class OrbitDiffEq:
    def __init__(self,reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0,t0):
        self.reducedmass=reducedmass
        self.xi=x0
        self.yi=y0
        self.zi=z0
        self.vxi=ux0
        self.vyi=uy0
        self.vzi=uz0
        self.axi=ax0
        self.ayi=ay0
        self.azi=az0
        self.ti=t0
    def dxidt(self,t):
        return self.vxi
    def dyidt(self,t):
        return self.vyi
    def dzidt(self,t):
        return self.vzi
    def dvxidt(self,t):
        #return axi[m]
        axii=np.zeros(np.shape(self.axi))
        rii=np.sqrt(self.xi**2+self.yi**2+self.zi**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(1,len(rii)):
                if j==0:
                    axii[j]=0.0
                if j!=k:
                    rreljk=np.abs((self.xi[j] - self.xi[k])**2+(self.yi[j]-self.yi[k])**2+(self.zi[j]-self.zi[k])**2)**(1./2.)
                    axii[j]-=Gconstant*self.reducedmass[k]*(self.xi[j]  - self.xi[k])/rreljk**3
        self.axi=axii
        return axii
    def dvyidt(self,t):
        #return axi[m]
        ayii=np.zeros(np.shape(self.ayi))
        rii=np.sqrt(self.xi**2+self.yi**2+self.zi**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(1,len(rii)):
                if j==0:
                    ayii[j]=0.0
                if j!=k:
                    rreljk=np.abs((self.xi[j] - self.xi[k])**2+(self.yi[j]-self.yi[k])**2+(self.zi[j]-self.zi[k])**2)**(1./2.)
                    ayii[j]-=Gconstant*self.reducedmass[k]*(self.yi[j]  - self.yi[k])/rreljk**3
        self.ayi=ayii
        return ayii
    def dvzidt(self,t):
        #return axi[m]
        azii=np.zeros(np.shape(self.azi))
        rii=np.sqrt(self.xi**2+self.yi**2+self.zi**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(1,len(rii)):
                if j==0:
                    azii[j]=0.0
                if j!=k:
                    rreljk=np.abs((self.xi[j] - self.xi[k])**2+(self.yi[j]-self.yi[k])**2+(self.zi[j]-self.zi[k])**2)**(1./2.)
                    azii[j]-=Gconstant*self.reducedmass[k]*(self.zi[j]  - self.zi[k])/rreljk**3
        self.azi=azii
        return azii
    def updateINTERNAL(self,xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii,tii):
        self.xi=xii
        self.yi=yii
        self.zi=zii
        self.vxi=vxii
        self.vyi=vyii
        self.vzi=vzii
        self.axi=axii
        self.ayi=ayii
        self.azi=azii
        self.ti=tii
        return self
    def update(self,xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii,tii):
        self.xi=xii
        self.yi=yii
        self.zi=zii
        self.vxi=vxii
        self.vyi=vyii
        self.vzi=vzii
        self.axi=axii
        self.ayi=ayii
        self.azi=azii
        self.ti=tii
    def print2D(self):
        print(self.reducedmass,self.xi,self.yi,self.zi,self.vxi,self.vyi,self.vzi, self.axi,self.ayi,self.azi, self.ti)
        return self
    def list2D(self):
        return self.reducedmass,self.xi,self.yi,self.vxi,self.vyi,self.axi,self.ayi,self.ti
    def timestepRK4ODE(self,step,dt):

    
        h=dt
        #tnew,ynew, intval=RK4(h,t,y,f)
        #m represents choices of mass
        i=step
        
        tnew,intvalx=RK4implicit(h,self.ti,self.xi,self.dxidt)
        xii = intvalx
        tnew,intvalvx=RK4implicit(h,self.ti,self.vxi,self.dvxidt)
        vxii=intvalvx
        tnew,intvaly=RK4implicit(h,self.ti,self.yi,self.dyidt)
        yii = intvaly
        tnew,intvalvy=RK4implicit(h,self.ti,self.vyi,self.dvyidt)
        vyii=intvalvy
        tnew,intvalz=RK4implicit(h,self.ti,self.zi,self.dzidt)
        zii = intvalz
        tnew,intvalvz=RK4implicit(h,self.ti,self.vzi,self.dvzidt)
        vzii=intvalvz
        axii=self.dvxidt(self.ti)
        ayii=self.dvyidt(self.ti)
        azii=self.dvzidt(self.ti)
 
        #print(xii)
        self.updateINTERNAL(xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii,self.ti+dt)
        return reducedmass, xii,yii,zii,vxii,vyii,vzii,self.axi,self.ayi,self.azi,self.ti

In [55]:
print(xyuvaeq)

(2.0, array([2. , 0.5]), array([  0., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0. , -0.2]), array([0., 0.]), array([-0.    ,  0.0008]), array([-0., -0.]), array([0., 0.]))


In [56]:
mtotal,reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0=xyuvaeqreducedmass
ODEeq= OrbitDiffEq(reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0,0.0)
ODEeq.print2D()
ODEeq.print2D()

[2.  0.5] [ 0. 50.] [0. 0.] [0. 0.] [-0. -0.] [0.  0.2] [0. 0.] [-0.     -0.0002] [-0. -0.] [0. 0.] 0.0
[2.  0.5] [ 0. 50.] [0. 0.] [0. 0.] [-0. -0.] [0.  0.2] [0. 0.] [-0.     -0.0002] [-0. -0.] [0. 0.] 0.0


In [57]:
mtotal,reducedmass,x,y,z,vx,vy,vz,ax,ay,az=xyuvaeqreducedmass
print(x,y,vx,vy,ax,ay)
print(xyuvaeq)

[ 0. 50.] [0. 0.] [-0. -0.] [0.  0.2] [-0.     -0.0002] [-0. -0.]
(2.0, array([2. , 0.5]), array([  0., -50.]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([ 0. , -0.2]), array([0., 0.]), array([-0.    ,  0.0008]), array([-0., -0.]), array([0., 0.]))


In [58]:
dt=1 #natural units #*31556926 #seconds per year
numsteps=3000
mtotal, reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0=xyuvaeqreducedmass
ODEeq= OrbitDiffEq(reducedmass,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0,0.0)
mtotal,reducedmass,x,y,z,vx,vy,vz,ax,ay,az=xyuvaeq
ODEeq.print2D()
t=0.0
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
for i in np.arange(1,numsteps):
    reducedmass,x,y,z,vx,vy,vz,ax,ay,az,t=ODEeq.timestepRK4ODE(i,dt)
    ODEeq.print2D()
    ODEeq.update(x,y,z,vx,vy,vz,ax,ay,az,t)
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])



[2.  0.5] [ 0. 50.] [0. 0.] [0. 0.] [-0. -0.] [0.  0.2] [0. 0.] [-0.     -0.0002] [-0. -0.] [0. 0.] 0.0
[2.  0.5] [ 0. 50.] [0.  0.2] [0. 0.] [ 0.     -0.0008] [0.  0.2] [0. 0.] [ 0.     -0.0008] [0. 0.] [0. 0.] 1.0
[2.  0.5] [ 0.     49.9992] [0.  0.4] [0. 0.] [ 0.         -0.00159998] [0.        0.1999968] [0. 0.] [ 0.         -0.00079998] [ 0.0000000e+00 -3.1999232e-06] [0. 0.] 2.0
[2.  0.5] [ 0.         49.99760002] [0.        0.5999968] [0. 0.] [ 0.         -0.00239993] [0.        0.1999904] [0. 0.] [ 0.         -0.00079995] [ 0.00000000e+00 -6.39969281e-06] [0. 0.] 3.0
[2.  0.5] [ 0.         49.99520009] [0.        0.7999872] [0. 0.] [ 0.         -0.00319983] [0.        0.1999808] [0. 0.] [ 0.        -0.0007999] [ 0.00000000e+00 -9.59925762e-06] [0. 0.] 4.0
[2.  0.5] [ 0.         49.99200026] [0.       0.999968] [0. 0.] [ 0.         -0.00399968] [0.       0.199968] [0. 0.] [ 0.         -0.00079985] [ 0.00000000e+00 -1.27985664e-05] [0. 0.] 5.0
[2.  0.5] [ 0.         49.98800058] 

[2.  0.5] [ 0.         47.49375063] [ 0.         15.73856765] [0. 0.] [ 0.         -0.06289321] [0.         0.18998176] [0. 0.] [ 0.         -0.00075938] [ 0.         -0.00024828] [0. 0.] 80.0
[2.  0.5] [ 0.         47.43085742] [ 0.         15.92854941] [0. 0.] [ 0.         -0.06365159] [0.         0.18973045] [0. 0.] [ 0.         -0.00075837] [ 0.         -0.00025131] [0. 0.] 81.0
[2.  0.5] [ 0.         47.36720583] [ 0.         16.11827987] [0. 0.] [ 0.         -0.06440893] [0.         0.18947612] [0. 0.] [ 0.         -0.00075735] [ 0.         -0.00025434] [0. 0.] 82.0
[2.  0.5] [ 0.        47.3027969] [ 0.         16.30775598] [0. 0.] [ 0.         -0.06516524] [0.         0.18921876] [0. 0.] [ 0.         -0.00075631] [ 0.         -0.00025736] [0. 0.] 83.0
[2.  0.5] [ 0.         47.23763166] [ 0.         16.49697474] [0. 0.] [ 0.        -0.0659205] [0.         0.18895838] [0. 0.] [ 0.         -0.00075526] [ 0.         -0.00026038] [0. 0.] 84.0
[2.  0.5] [ 0.         47.17171116] [ 0

[2.  0.5] [ 0.         41.77157123] [ 0.         27.60326883] [0. 0.] [ 0.       -0.110206] [0.         0.16713035] [0. 0.] [ 0.         -0.00066739] [ 0.        -0.0004372] [0. 0.] 146.0
[2.  0.5] [ 0.         41.66136523] [ 0.         27.77039918] [0. 0.] [ 0.         -0.11087162] [0.        0.1666905] [0. 0.] [ 0.         -0.00066563] [ 0.         -0.00043986] [0. 0.] 147.0
[2.  0.5] [ 0.         41.55049361] [ 0.         27.93708967] [0. 0.] [ 0.         -0.11153547] [0.         0.16624799] [0. 0.] [ 0.         -0.00066385] [ 0.        -0.0004425] [0. 0.] 148.0
[2.  0.5] [ 0.         41.43895814] [ 0.         28.10333767] [0. 0.] [ 0.         -0.11219752] [0.         0.16580285] [0. 0.] [ 0.         -0.00066206] [ 0.         -0.00044514] [0. 0.] 149.0
[2.  0.5] [ 0.         41.32676061] [ 0.         28.26914052] [0. 0.] [ 0.         -0.11285778] [0.         0.16535507] [0. 0.] [ 0.         -0.00066025] [ 0.         -0.00044778] [0. 0.] 150.0
[2.  0.5] [ 0.         41.21390283] [ 0.

[2.  0.5] [ 0.         31.79151145] [ 0.        38.7482357] [0. 0.] [ 0.         -0.15451328] [0.        0.1273357] [0. 0.] [ 0.         -0.00050746] [ 0.         -0.00061349] [0. 0.] 221.0
[2.  0.5] [ 0.         31.63699817] [ 0.        38.8755714] [0. 0.] [ 0.         -0.15501827] [0.         0.12672021] [0. 0.] [ 0.         -0.00050499] [ 0.         -0.00061549] [0. 0.] 222.0
[2.  0.5] [ 0.        31.4819799] [ 0.         39.00229161] [0. 0.] [ 0.         -0.15552077] [0.         0.12610273] [0. 0.] [ 0.         -0.00050251] [ 0.         -0.00061748] [0. 0.] 223.0
[2.  0.5] [ 0.         31.32645912] [ 0.         39.12839435] [0. 0.] [ 0.         -0.15602079] [0.         0.12548327] [0. 0.] [ 0.         -0.00050002] [ 0.         -0.00061946] [0. 0.] 224.0
[2.  0.5] [ 0.         31.17043833] [ 0.         39.25387762] [0. 0.] [ 0.         -0.15651832] [0.         0.12486184] [0. 0.] [ 0.         -0.00049752] [ 0.         -0.00062143] [0. 0.] 225.0
[2.  0.5] [ 0.         31.01392001] [ 

[2.  0.5] [ 0.         20.08163674] [ 0.         45.99518543] [0. 0.] [ 0.         -0.18316506] [0.         0.08074964] [0. 0.] [ 0.         -0.00032062] [ 0.         -0.00072645] [0. 0.] 290.0
[2.  0.5] [ 0.         19.89847169] [ 0.         46.07593507] [0. 0.] [ 0.         -0.18348277] [0.         0.08002196] [0. 0.] [ 0.         -0.00031771] [ 0.         -0.00072769] [0. 0.] 291.0
[2.  0.5] [ 0.         19.71498892] [ 0.         46.15595703] [0. 0.] [ 0.         -0.18379756] [0.         0.07929304] [0. 0.] [ 0.         -0.00031479] [ 0.         -0.00072892] [0. 0.] 292.0
[2.  0.5] [ 0.         19.53119136] [ 0.         46.23525007] [0. 0.] [ 0.         -0.18410943] [0.         0.07856291] [0. 0.] [ 0.         -0.00031187] [ 0.         -0.00073013] [0. 0.] 293.0
[2.  0.5] [ 0.         19.34708194] [ 0.         46.31381298] [0. 0.] [ 0.         -0.18441836] [0.         0.07783157] [0. 0.] [ 0.         -0.00030894] [ 0.         -0.00073134] [0. 0.] 294.0
[2.  0.5] [ 0.         19.1626

...

[2.  0.5] [  0.         -29.54739186] [  0.         -45.65787827] [0. 0.] [0.         0.15964978] [ 0.        -0.1053108] [0. 0.] [0.         0.00036941] [0.         0.00056644] [0. 0.] 2764.0
[2.  0.5] [  0.         -29.38774208] [  0.         -45.76318908] [0. 0.] [0.         0.16001716] [ 0.         -0.10474311] [0. 0.] [0.         0.00036738] [0.        0.0005677] [0. 0.] 2765.0
[2.  0.5] [  0.         -29.22772492] [  0.         -45.86793218] [0. 0.] [0.         0.16038252] [ 0.         -0.10417416] [0. 0.] [0.         0.00036536] [0.         0.00056894] [0. 0.] 2766.0
[2.  0.5] [  0.         -29.06734241] [  0.         -45.97210634] [0. 0.] [0.         0.16074585] [ 0.         -0.10360398] [0. 0.] [0.         0.00036333] [0.         0.00057018] [0. 0.] 2767.0
[2.  0.5] [  0.         -28.90659656] [  0.         -46.07571033] [0. 0.] [0.         0.16110714] [ 0.         -0.10303257] [0. 0.] [0.        0.0003613] [0.         0.00057141] [0. 0.] 2768.0
[2.  0.5] [  0.         -28.745

[2.  0.5] [  0.         -17.59895206] [  0.         -51.59717824] [0. 0.] [0.         0.18027714] [ 0.         -0.06296745] [0. 0.] [0.         0.00021949] [0.        0.0006362] [0. 0.] 2834.0
[2.  0.5] [  0.         -17.41867491] [  0.         -51.66014569] [0. 0.] [0.         0.18049439] [ 0.         -0.06233053] [0. 0.] [0.         0.00021724] [0.         0.00063692] [0. 0.] 2835.0
[2.  0.5] [  0.         -17.23818053] [  0.         -51.72247621] [0. 0.] [0.         0.18070938] [ 0.         -0.06169289] [0. 0.] [0.       0.000215] [0.         0.00063764] [0. 0.] 2836.0
[2.  0.5] [  0.         -17.05747114] [  0.        -51.7841691] [0. 0.] [0.         0.18092213] [ 0.         -0.06105455] [0. 0.] [0.         0.00021275] [0.         0.00063834] [0. 0.] 2837.0
[2.  0.5] [  0.         -16.87654901] [  0.         -51.84522365] [0. 0.] [0.         0.18113263] [ 0.        -0.0604155] [0. 0.] [0.        0.0002105] [0.         0.00063905] [0. 0.] 2838.0
[2.  0.5] [  0.         -16.69541638]

[2.  0.5] [ 0.         -8.36344206] [  0.         -53.95310192] [0. 0.] [0.         0.18835109] [ 0.         -0.03039896] [0. 0.] [0.        0.0001051] [0.        0.0006627] [0. 0.] 2884.0
[2.  0.5] [ 0.         -8.17509097] [  0.         -53.98350088] [0. 0.] [0.         0.18845387] [ 0.         -0.02973594] [0. 0.] [0.         0.00010278] [0.         0.00066302] [0. 0.] 2885.0
[2.  0.5] [ 0.        -7.9866371] [  0.         -54.01323681] [0. 0.] [0.         0.18855432] [ 0.        -0.0290726] [0. 0.] [0.         0.00010045] [0.         0.00066334] [0. 0.] 2886.0
[2.  0.5] [ 0.         -7.79808278] [  0.         -54.04230941] [0. 0.] [0.         0.18865245] [ 0.         -0.02840894] [0. 0.] [0.0000000e+00 9.8130442e-05] [0.         0.00066365] [0. 0.] 2887.0
[2.  0.5] [ 0.         -7.60943032] [  0.         -54.07071835] [0. 0.] [0.         0.18874826] [ 0.         -0.02774499] [0. 0.] [0.00000000e+00 9.58057448e-05] [0.         0.00066395] [0. 0.] 2888.0
[2.  0.5] [ 0.         -7.420

[2.  0.5] [ 0.        -0.0096189] [  0.         -54.66031636] [0. 0.] [0.         0.19066812] [ 0.         -0.00103168] [0. 0.] [0.00000000e+00 2.45297351e-06] [0.         0.00066943] [0. 0.] 2928.0
[2.  0.5] [0.         0.18104922] [  0.         -54.66134803] [0. 0.] [0.         0.19066824] [ 0.         -0.00036228] [0. 0.] [0.00000000e+00 1.17798283e-07] [0.        0.0006694] [0. 0.] 2929.0
[2.  0.5] [0.         0.37171746] [  0.         -54.66171031] [0. 0.] [0.         0.19066602] [0.         0.00030709] [0. 0.] [ 0.00000000e+00 -2.21706533e-06] [0.         0.00066936] [0. 0.] 2930.0
[2.  0.5] [0.         0.56238348] [  0.         -54.66140322] [0. 0.] [0.         0.19066147] [0.         0.00097641] [0. 0.] [ 0.00000000e+00 -4.55159046e-06] [0.         0.00066932] [0. 0.] 2931.0
[2.  0.5] [0.         0.75304494] [  0.         -54.66042681] [0. 0.] [0.         0.19065458] [0.         0.00164567] [0. 0.] [ 0.00000000e+00 -6.88575022e-06] [0.         0.00066927] [0. 0.] 2932.0
[2.  0.

[2.  0.5] [ 0.         12.46836916] [  0.         -53.29996641] [0. 0.] [0.         0.18570234] [0.         0.04270562] [0. 0.] [ 0.         -0.00014978] [0.         0.00065048] [0. 0.] 2994.0
[2.  0.5] [ 0.         12.65407151] [  0.         -53.25726079] [0. 0.] [0.         0.18555031] [0.         0.04335556] [0. 0.] [ 0.         -0.00015204] [0.         0.00064993] [0. 0.] 2995.0
[2.  0.5] [ 0.         12.83962181] [  0.         -53.21390523] [0. 0.] [0.         0.18539601] [0.         0.04400493] [0. 0.] [ 0.         -0.00015429] [0.         0.00064938] [0. 0.] 2996.0
[2.  0.5] [ 0.         13.02501783] [  0.        -53.1699003] [0. 0.] [0.         0.18523947] [0.         0.04465374] [0. 0.] [ 0.         -0.00015655] [0.         0.00064881] [0. 0.] 2997.0
[2.  0.5] [ 0.         13.21025729] [  0.         -53.12524656] [0. 0.] [0.         0.18508067] [0.         0.04530198] [0. 0.] [ 0.        -0.0001588] [0.         0.00064824] [0. 0.] 2998.0
[2.  0.5] [ 0.         13.39533796] [  

In [59]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Circular orbit, Reduced Mass, RK4 Method, Equal Mass", plot_width=400, plot_height=400)

# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(xcoord1,ycoord1, size=15, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="M")
p.circle(xcoord2,ycoord2, size=1, line_color="blue", fill_color="blue", fill_alpha=0.5,legend="mu")

p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

Circular orbit with RK4 method looks really good. Next step is to test the convergence of the L0 error.

In [60]:
def RunFirstOrbit(dt,initcondition,printoutput):
    masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=initcondition
    x0=x[1]
    lastvalue=[1,1]
    thisvalue=[x[1],y[1]]
    i=1
    while not (lastvalue[0]>0 and lastvalue[1]<0 and thisvalue[0]> 0 and thisvalue[1]>=0):
        t=0.+i*numsteps*dt
        mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
        if printoutput:
            print(x,y,vx,vy,ax,ay)
        #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
        #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
        #print(ax)
        xy=[x,y]
        xyt=np.transpose(xy)
        lastvalue,thisvalue=thisvalue, xyt[1]
        #lastvalue=thisvalue
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        #thisvalue[0]=x[1]
        #thisvalue[1]=y[1]
        if printoutput:
            print(x,y,lastvalue,thisvalue)
        i+=1
    
    print(thisvalue[0], thisvalue[1], lastvalue[0], lastvalue[1], x0, y0)
    return np.abs(x0-(thisvalue[0]+lastvalue[0])/2.)

In [61]:
dt=1 #*31556926 #seconds per year
numsteps=2000
mtotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeqreducedmass
L0arr=[]
dtarr=[]
dtinit=0.125/4.
for i in np.arange(6):
    dt=(2**i)*dtinit
    dtarr.append(dt)
    L0=RunFirstOrbit(dt,xyuvaeqreducedmass,False)
    L0arr.append(L0)
print(dtarr, L0arr)

23.348341288988056 0.0008665541491415284 23.34258151909529 -0.001518576423720374 50.0 [0. 0.]
23.60619561082283 0.0024587772869226737 23.594728215986205 -0.002354195229230498 50.0 [0. 0.]
24.104532144405788 0.0011735566528480682 24.081800044018003 -0.008607377977503501 50.0 [0. 0.]
25.12302900827314 0.0192042081893691 25.078378523129516 -0.0009712873626647259 50.0 [0. 0.]
26.982417281868326 0.012143498268046303 26.896089157838055 -0.029995025919710844 50.0 [0. 0.]
30.62945804571102 0.08507189980989394 30.467841913721433 -0.0046509304753436925 50.0 [0. 0.]
[0.03125, 0.0625, 0.125, 0.25, 0.5, 1.0] [26.65453859595833, 26.399538086595484, 25.906833905788105, 24.899296234298674, 23.060746780146808, 19.451350020283776]


In [62]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="RK4 method converges, equal mass", x_axis_label="1/dt", y_axis_label="L0 error", plot_width=400, plot_height=400)
harr=list(map(lambda x: 1./x, dtarr))
powfifthlaw=list(map(lambda x: 5*(x**0.20)+18,harr))
powfourthlaw=list(map(lambda x: 5*(x**0.25)+17,harr))
powsixthlaw=list(map(lambda x: 5*(x**(1./6.))+19,harr))
print(L0arr)
print(harr)
print(powfifthlaw)
print(powfourthlaw)

#print(pow4arr)
# add a circle renderer with x and y coordinates, size, color, and alpha
p.circle(harr,L0arr, size=15, line_color="blue",fill_color="blue", fill_alpha=0.5, legend="L0")
p.line(harr,powfifthlaw, line_color="green",legend="h^1/5")
p.line(harr,powfourthlaw, line_color="orange",legend="h^1/4")
p.line(harr,powsixthlaw, line_color="purple",legend="h^1/6")
p.legend.location = "bottom_right"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

[26.65453859595833, 26.399538086595484, 25.906833905788105, 24.899296234298674, 23.060746780146808, 19.451350020283776]
[32.0, 16.0, 8.0, 4.0, 2.0, 1.0]
[28.0, 26.70550563296124, 25.57858283255199, 24.597539553864472, 23.743491774985173, 23.0]
[28.89207115002721, 27.0, 25.408964152537145, 24.071067811865476, 22.946035575013603, 22.0]


As 1/dt goes to zero, the L0 error goes to zero. That's good. That's convergence. 

The power law with which it does it appears to be h=1/dt to the fifth or sixth or higher. Runga Kutta fourth order expects fourth order convergence of the total cumulative error and fifth order convergence of a single points error. This is a single points error I am measuring. So fifth order convergence is expected, and sixth order convergence is a nice bonus if it is really seen, which is difficult to tell from the sparsity of data in the fit. It is probably not worth doing longer and more precise runs to distinguish between superconvergence and convergence for these purposes. 